In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.nn.init as init
from torch.autograd import Variable

In [2]:
__all__ = ['ResNet', 'resnet20', 'resnet32', 'resnet44', 'resnet56', 'resnet110', 'resnet1202']

def _weights_init(m):
  classname = m.__class__.__name__
  #print(classname)
  if isinstance(m, nn.Linear) or isinstance(m, nn.Conv2d):
      init.kaiming_normal_(m.weight)

class LambdaLayer(nn.Module):
  def __init__(self, lambd):
    super(LambdaLayer, self).__init__()
    self.lambd = lambd

  def forward(self, x):
    return self.lambd(x)

In [3]:
class BasicBlock(nn.Module):
  # block 안에서 plane 수 증가 비율
  expansion = 1

  # in_planes : input, planes: output
  def __init__(self, in_planes, planes, stride=1, option='A'):
    super(BasicBlock, self).__init__()
    
    self.dropout = nn.Dropout(0.4)
    
    self.conv1 = nn.Conv2d(in_planes, planes, kernel_size=3, stride=stride, padding=1, bias=False)
    self.bn1 = nn.BatchNorm2d(planes)
    
    self.conv2 = nn.Conv2d(planes, planes, kernel_size=3,stride=1,padding=1,bias=False)
    self.bn2 = nn.BatchNorm2d(planes)
    
    self.shortcut = nn.Sequential()
    # shortcut connection 시 shape가 맞지 않을 때(conv_n 이 conv_n+1로 넘어갈 때)
    if stride != 1 or in_planes != planes:
        if option == 'A':
          # zero padding
          self.shortcut = LambdaLayer(lambda x:
                                      F.pad(x[:, :, ::2, ::2], (0, 0, 0, 0, planes//4, planes//4), "constant", 0))
        elif option == 'B':
          # projection
          self.shortcut = nn.Sequential(
              nn.Conv2d(in_planes, self.expansion * planes, kernel_size=1, stride=stride, bias=False),
              nn.BatchNorm2d(self.expansion * planes)
              )

  def forward(self, x):
    out = F.relu(self.bn1(self.conv1(x)))
    
    #out = self.dropout(out)
    
    out = self.bn2(self.conv2(out))
    # shortcut connection
    out += self.shortcut(x)
    out = F.relu(out)
    return out


In [17]:
class ResNet(nn.Module):
  def __init__(self, block, num_blocks, num_classes=10):
    super(ResNet, self).__init__()
    
    self.in_planes = 16

    self.dropout = nn.Dropout()

    self.conv1 = nn.Conv2d(3, 16, kernel_size=3, stride=1, padding=1, bias=False)
    self.bn1 = nn.BatchNorm2d(16)


    # feature map : 32 x 32 x 16
    self.layer1 = self._make_layer(block, 16, num_blocks[0], stride=1)
    # feature map : 16 x 16 x 32
    self.layer2 = self._make_layer(block, 32, num_blocks[1], stride=2)
    # feature map : 8 x 8 x 64
    self.layer3 = self._make_layer(block, 64, num_blocks[2], stride=2)
    # 마지막 클래스 예측 (Linear)
    self.fc_out = nn.Linear(64, num_classes)

    self.apply(_weights_init)

  
  def _make_layer(self, block, planes, num_blocks, stride):
    # 처음 stride만 2, 이후 1
    strides = [stride] + [1]*(num_blocks-1)
    layers = []
    for stride in strides:
        layers.append(block(self.in_planes, planes, stride))
        self.in_planes = planes * block.expansion
    return nn.Sequential(*layers)

  def forward(self, x):
    out = F.relu(self.bn1(self.conv1(x)))
    #out = self.dropout(out)
    out = self.layer1(out)
    out = self.dropout(out)
    out = self.layer2(out)
    out = self.dropout(out)
    out = self.layer3(out)
    out = F.avg_pool2d(out, out.size()[3])
    out = out.view(out.size(0),-1)
    out = self.fc_out(out)
    return out

In [5]:
def resnet20():
    return ResNet(BasicBlock, [3, 3, 3])


def resnet32():
    return ResNet(BasicBlock, [5, 5, 5])


def resnet44():
    return ResNet(BasicBlock, [7, 7, 7])


def resnet56():
    return ResNet(BasicBlock, [9, 9, 9])
# def resnet56():
#     return ResNet(Bottleneck, [9, 9, 9])


def resnet110():
    return ResNet(BasicBlock, [18, 18, 18])


def resnet1202():
    return ResNet(BasicBlock, [200, 200, 200])

In [6]:
import torchvision
import torchvision.transforms as transforms
import torch.backends.cudnn as cudnn
import torch.optim as optim
import os
import argparse

In [7]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [8]:
transform_train = transforms.Compose([
                                      transforms.RandomCrop(32, padding=4),
                                      transforms.RandomHorizontalFlip(),
                                      transforms.ToTensor(),
                                      transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
])

transform_test = transforms.Compose([
                                     transforms.ToTensor(),
                                     transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
])

trainset = torchvision.datasets.CIFAR10(
    root='./data',train=True,download=True,transform=transform_train)
trainloader = torch.utils.data.DataLoader(
    trainset, batch_size=128,shuffle=True,num_workers=2
)
testset = torchvision.datasets.CIFAR10(
    root='./data',train=False,download=True,transform=transform_test)
testloader = torch.utils.data.DataLoader(
    testset, batch_size=100,shuffle=False,num_workers=2
)
classes=('plane','car','bird','cat','deer','dog','frog','horse','ship','truck')

Files already downloaded and verified
Files already downloaded and verified


In [9]:
def train(epoch):
  net.train()
  train_loss = 0
  correct = 0
  total = 0
  for batch_idx, (inputs, targets) in enumerate(trainloader):
    inputs, targets = inputs.to(device), targets.to(device)
    
    optimizer.zero_grad()
    outputs = net(inputs)
    loss = criterion(outputs, targets)
    loss.backward()
    optimizer.step()

    train_loss += loss.item()
    _, predicted = outputs.max(1)
    total += targets.size(0)
    correct += predicted.eq(targets).sum().item()
    if batch_idx % 10 == 0:
      print(batch_idx, len(trainloader), 'Loss: %.3f | Acc: %.3f%% (%d/%d)'%(train_loss/(batch_idx+1), 100.*correct/total, correct, total))


In [12]:
def test(epoch):
  global best_accuracy
  net.eval()
  test_loss = 0
  correct = 0
  total = 0
  with torch.no_grad():
    for batch_idx, (inputs, targets) in enumerate(testloader):
      inputs, targets = inputs.to(device), targets.to(device)
      ouputs = net(inputs)
      loss = criterion(ouputs, targets)
      
      test_loss += loss.item()
      _, predicted = ouputs.max(1)
      total += targets.size(0)
      correct += predicted.eq(targets).sum().item()
      if batch_idx % 50 == 0:
        print(batch_idx, len(testloader), 'Loss: %.3f | Acc: %.3f%% (%d/%d)'%(test_loss/(batch_idx+1), 100.*correct/total, correct, total))
  acc = 100.*correct/total
  if acc > best_accuracy:
      print('Saving..')
      best_accuracy = acc

In [25]:
best_accuracy = 0
start_epoch = 0

In [26]:
net = resnet20()
net = net.to(device)
if device == 'cuda':
  net = torch.nn.DataParallel(net)
  cudnn.benchmark = True

In [27]:
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
#optimizer = optim.Adam(net.parameters(), lr=0.1, weight_decay=1e-4)

#optimizer = optim.SGD(net.parameters(), lr=0.1,momentum=0.9, weight_decay=1e-4)
#decay_epoch = [32000, 48000]
#scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=decay_epoch, gamma=0.1)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

In [16]:
for epoch in range(start_epoch, start_epoch+200):
  train(epoch)
  test(epoch)
  scheduler.step()
  print('epoch : ',epoch, best_accuracy)

0 391 Loss: 3.099 | Acc: 10.156% (13/128)
10 391 Loss: 2.605 | Acc: 11.932% (168/1408)
20 391 Loss: 2.451 | Acc: 14.881% (400/2688)
30 391 Loss: 2.348 | Acc: 15.902% (631/3968)
40 391 Loss: 2.281 | Acc: 17.702% (929/5248)
50 391 Loss: 2.223 | Acc: 19.547% (1276/6528)
60 391 Loss: 2.176 | Acc: 20.633% (1611/7808)
70 391 Loss: 2.136 | Acc: 21.699% (1972/9088)
80 391 Loss: 2.098 | Acc: 22.753% (2359/10368)
90 391 Loss: 2.067 | Acc: 23.910% (2785/11648)
100 391 Loss: 2.043 | Acc: 24.876% (3216/12928)
110 391 Loss: 2.016 | Acc: 25.873% (3676/14208)
120 391 Loss: 1.999 | Acc: 26.608% (4121/15488)
130 391 Loss: 1.981 | Acc: 27.141% (4551/16768)
140 391 Loss: 1.960 | Acc: 27.804% (5018/18048)
150 391 Loss: 1.946 | Acc: 28.296% (5469/19328)
160 391 Loss: 1.932 | Acc: 28.775% (5930/20608)
170 391 Loss: 1.920 | Acc: 29.158% (6382/21888)
180 391 Loss: 1.908 | Acc: 29.446% (6822/23168)
190 391 Loss: 1.897 | Acc: 29.806% (7287/24448)
200 391 Loss: 1.884 | Acc: 30.278% (7790/25728)
210 391 Loss: 1.87

20 391 Loss: 1.039 | Acc: 62.388% (1677/2688)
30 391 Loss: 1.028 | Acc: 63.029% (2501/3968)
40 391 Loss: 1.037 | Acc: 62.691% (3290/5248)
50 391 Loss: 1.038 | Acc: 62.699% (4093/6528)
60 391 Loss: 1.040 | Acc: 62.551% (4884/7808)
70 391 Loss: 1.038 | Acc: 62.786% (5706/9088)
80 391 Loss: 1.035 | Acc: 63.204% (6553/10368)
90 391 Loss: 1.032 | Acc: 63.281% (7371/11648)
100 391 Loss: 1.027 | Acc: 63.521% (8212/12928)
110 391 Loss: 1.026 | Acc: 63.528% (9026/14208)
120 391 Loss: 1.026 | Acc: 63.443% (9826/15488)
130 391 Loss: 1.027 | Acc: 63.317% (10617/16768)
140 391 Loss: 1.027 | Acc: 63.320% (11428/18048)
150 391 Loss: 1.027 | Acc: 63.354% (12245/19328)
160 391 Loss: 1.027 | Acc: 63.378% (13061/20608)
170 391 Loss: 1.026 | Acc: 63.418% (13881/21888)
180 391 Loss: 1.022 | Acc: 63.501% (14712/23168)
190 391 Loss: 1.022 | Acc: 63.568% (15541/24448)
200 391 Loss: 1.020 | Acc: 63.631% (16371/25728)
210 391 Loss: 1.020 | Acc: 63.577% (17171/27008)
220 391 Loss: 1.018 | Acc: 63.670% (18011/282

30 391 Loss: 0.794 | Acc: 71.799% (2849/3968)
40 391 Loss: 0.792 | Acc: 72.104% (3784/5248)
50 391 Loss: 0.788 | Acc: 72.074% (4705/6528)
60 391 Loss: 0.789 | Acc: 72.157% (5634/7808)
70 391 Loss: 0.788 | Acc: 72.249% (6566/9088)
80 391 Loss: 0.789 | Acc: 72.328% (7499/10368)
90 391 Loss: 0.786 | Acc: 72.459% (8440/11648)
100 391 Loss: 0.782 | Acc: 72.563% (9381/12928)
110 391 Loss: 0.776 | Acc: 72.783% (10341/14208)
120 391 Loss: 0.775 | Acc: 72.818% (11278/15488)
130 391 Loss: 0.773 | Acc: 72.937% (12230/16768)
140 391 Loss: 0.771 | Acc: 73.044% (13183/18048)
150 391 Loss: 0.773 | Acc: 73.003% (14110/19328)
160 391 Loss: 0.771 | Acc: 73.132% (15071/20608)
170 391 Loss: 0.770 | Acc: 73.104% (16001/21888)
180 391 Loss: 0.767 | Acc: 73.230% (16966/23168)
190 391 Loss: 0.769 | Acc: 73.229% (17903/24448)
200 391 Loss: 0.768 | Acc: 73.290% (18856/25728)
210 391 Loss: 0.769 | Acc: 73.178% (19764/27008)
220 391 Loss: 0.769 | Acc: 73.183% (20702/28288)
230 391 Loss: 0.768 | Acc: 73.184% (2163

40 391 Loss: 0.618 | Acc: 79.021% (4147/5248)
50 391 Loss: 0.614 | Acc: 79.013% (5158/6528)
60 391 Loss: 0.616 | Acc: 78.804% (6153/7808)
70 391 Loss: 0.613 | Acc: 78.895% (7170/9088)
80 391 Loss: 0.612 | Acc: 78.916% (8182/10368)
90 391 Loss: 0.612 | Acc: 78.803% (9179/11648)
100 391 Loss: 0.608 | Acc: 78.937% (10205/12928)
110 391 Loss: 0.610 | Acc: 78.899% (11210/14208)
120 391 Loss: 0.611 | Acc: 78.939% (12226/15488)
130 391 Loss: 0.615 | Acc: 78.781% (13210/16768)
140 391 Loss: 0.616 | Acc: 78.635% (14192/18048)
150 391 Loss: 0.616 | Acc: 78.663% (15204/19328)
160 391 Loss: 0.616 | Acc: 78.581% (16194/20608)
170 391 Loss: 0.618 | Acc: 78.449% (17171/21888)
180 391 Loss: 0.621 | Acc: 78.406% (18165/23168)
190 391 Loss: 0.618 | Acc: 78.530% (19199/24448)
200 391 Loss: 0.617 | Acc: 78.525% (20203/25728)
210 391 Loss: 0.618 | Acc: 78.547% (21214/27008)
220 391 Loss: 0.621 | Acc: 78.471% (22198/28288)
230 391 Loss: 0.621 | Acc: 78.473% (23203/29568)
240 391 Loss: 0.622 | Acc: 78.436% (

50 391 Loss: 0.539 | Acc: 81.924% (5348/6528)
60 391 Loss: 0.545 | Acc: 81.493% (6363/7808)
70 391 Loss: 0.544 | Acc: 81.437% (7401/9088)
80 391 Loss: 0.554 | Acc: 80.826% (8380/10368)
90 391 Loss: 0.553 | Acc: 80.761% (9407/11648)
100 391 Loss: 0.554 | Acc: 80.670% (10429/12928)
110 391 Loss: 0.555 | Acc: 80.638% (11457/14208)
120 391 Loss: 0.553 | Acc: 80.688% (12497/15488)
130 391 Loss: 0.549 | Acc: 80.850% (13557/16768)
140 391 Loss: 0.548 | Acc: 80.884% (14598/18048)
150 391 Loss: 0.552 | Acc: 80.743% (15606/19328)
160 391 Loss: 0.553 | Acc: 80.697% (16630/20608)
170 391 Loss: 0.548 | Acc: 80.894% (17706/21888)
180 391 Loss: 0.547 | Acc: 80.939% (18752/23168)
190 391 Loss: 0.547 | Acc: 80.923% (19784/24448)
200 391 Loss: 0.547 | Acc: 80.955% (20828/25728)
210 391 Loss: 0.548 | Acc: 80.917% (21854/27008)
220 391 Loss: 0.548 | Acc: 80.939% (22896/28288)
230 391 Loss: 0.548 | Acc: 80.922% (23927/29568)
240 391 Loss: 0.549 | Acc: 80.897% (24955/30848)
250 391 Loss: 0.550 | Acc: 80.917

...

50 391 Loss: 0.049 | Acc: 98.591% (6436/6528)
60 391 Loss: 0.051 | Acc: 98.553% (7695/7808)
70 391 Loss: 0.051 | Acc: 98.504% (8952/9088)
80 391 Loss: 0.051 | Acc: 98.544% (10217/10368)
90 391 Loss: 0.050 | Acc: 98.583% (11483/11648)
100 391 Loss: 0.050 | Acc: 98.592% (12746/12928)
110 391 Loss: 0.050 | Acc: 98.620% (14012/14208)
120 391 Loss: 0.049 | Acc: 98.644% (15278/15488)
130 391 Loss: 0.048 | Acc: 98.652% (16542/16768)
140 391 Loss: 0.050 | Acc: 98.604% (17796/18048)
150 391 Loss: 0.050 | Acc: 98.603% (19058/19328)
160 391 Loss: 0.049 | Acc: 98.622% (20324/20608)
170 391 Loss: 0.049 | Acc: 98.625% (21587/21888)
180 391 Loss: 0.050 | Acc: 98.619% (22848/23168)
190 391 Loss: 0.049 | Acc: 98.638% (24115/24448)
200 391 Loss: 0.050 | Acc: 98.609% (25370/25728)
210 391 Loss: 0.050 | Acc: 98.604% (26631/27008)
220 391 Loss: 0.049 | Acc: 98.625% (27899/28288)
230 391 Loss: 0.050 | Acc: 98.596% (29153/29568)
240 391 Loss: 0.050 | Acc: 98.609% (30419/30848)
250 391 Loss: 0.050 | Acc: 98.5

60 391 Loss: 0.055 | Acc: 98.438% (7686/7808)
70 391 Loss: 0.055 | Acc: 98.426% (8945/9088)
80 391 Loss: 0.054 | Acc: 98.447% (10207/10368)
90 391 Loss: 0.053 | Acc: 98.532% (11477/11648)
100 391 Loss: 0.052 | Acc: 98.538% (12739/12928)
110 391 Loss: 0.052 | Acc: 98.522% (13998/14208)
120 391 Loss: 0.051 | Acc: 98.560% (15265/15488)
130 391 Loss: 0.051 | Acc: 98.545% (16524/16768)
140 391 Loss: 0.051 | Acc: 98.532% (17783/18048)
150 391 Loss: 0.051 | Acc: 98.536% (19045/19328)
160 391 Loss: 0.051 | Acc: 98.481% (20295/20608)
170 391 Loss: 0.051 | Acc: 98.488% (21557/21888)
180 391 Loss: 0.051 | Acc: 98.489% (22818/23168)
190 391 Loss: 0.051 | Acc: 98.499% (24081/24448)
200 391 Loss: 0.051 | Acc: 98.496% (25341/25728)
210 391 Loss: 0.051 | Acc: 98.478% (26597/27008)
220 391 Loss: 0.051 | Acc: 98.487% (27860/28288)
230 391 Loss: 0.050 | Acc: 98.509% (29127/29568)
240 391 Loss: 0.050 | Acc: 98.512% (30389/30848)
250 391 Loss: 0.051 | Acc: 98.490% (31643/32128)
260 391 Loss: 0.051 | Acc: 9

70 391 Loss: 0.045 | Acc: 98.801% (8979/9088)
80 391 Loss: 0.046 | Acc: 98.765% (10240/10368)
90 391 Loss: 0.047 | Acc: 98.772% (11505/11648)
100 391 Loss: 0.048 | Acc: 98.739% (12765/12928)
110 391 Loss: 0.048 | Acc: 98.698% (14023/14208)
120 391 Loss: 0.047 | Acc: 98.709% (15288/15488)
130 391 Loss: 0.048 | Acc: 98.682% (16547/16768)
140 391 Loss: 0.047 | Acc: 98.709% (17815/18048)
150 391 Loss: 0.048 | Acc: 98.691% (19075/19328)
160 391 Loss: 0.047 | Acc: 98.709% (20342/20608)
170 391 Loss: 0.047 | Acc: 98.712% (21606/21888)
180 391 Loss: 0.048 | Acc: 98.684% (22863/23168)
190 391 Loss: 0.048 | Acc: 98.695% (24129/24448)
200 391 Loss: 0.047 | Acc: 98.698% (25393/25728)
210 391 Loss: 0.048 | Acc: 98.700% (26657/27008)
220 391 Loss: 0.047 | Acc: 98.706% (27922/28288)
230 391 Loss: 0.047 | Acc: 98.708% (29186/29568)
240 391 Loss: 0.047 | Acc: 98.700% (30447/30848)
250 391 Loss: 0.047 | Acc: 98.687% (31706/32128)
260 391 Loss: 0.047 | Acc: 98.668% (32963/33408)
270 391 Loss: 0.047 | Acc

80 391 Loss: 0.050 | Acc: 98.679% (10231/10368)
90 391 Loss: 0.049 | Acc: 98.678% (11494/11648)
100 391 Loss: 0.049 | Acc: 98.677% (12757/12928)
110 391 Loss: 0.050 | Acc: 98.649% (14016/14208)
120 391 Loss: 0.049 | Acc: 98.651% (15279/15488)
130 391 Loss: 0.049 | Acc: 98.658% (16543/16768)
140 391 Loss: 0.049 | Acc: 98.665% (17807/18048)
150 391 Loss: 0.049 | Acc: 98.660% (19069/19328)
160 391 Loss: 0.049 | Acc: 98.656% (20331/20608)
170 391 Loss: 0.050 | Acc: 98.643% (21591/21888)
180 391 Loss: 0.049 | Acc: 98.645% (22854/23168)
190 391 Loss: 0.049 | Acc: 98.646% (24117/24448)
200 391 Loss: 0.049 | Acc: 98.636% (25377/25728)
210 391 Loss: 0.049 | Acc: 98.652% (26644/27008)
220 391 Loss: 0.049 | Acc: 98.657% (27908/28288)
230 391 Loss: 0.049 | Acc: 98.644% (29167/29568)
240 391 Loss: 0.049 | Acc: 98.651% (30432/30848)
250 391 Loss: 0.048 | Acc: 98.643% (31692/32128)
260 391 Loss: 0.048 | Acc: 98.629% (32950/33408)
270 391 Loss: 0.048 | Acc: 98.622% (34210/34688)
280 391 Loss: 0.049 | 

90 391 Loss: 0.052 | Acc: 98.412% (11463/11648)
100 391 Loss: 0.052 | Acc: 98.453% (12728/12928)
110 391 Loss: 0.052 | Acc: 98.438% (13986/14208)
120 391 Loss: 0.053 | Acc: 98.392% (15239/15488)
130 391 Loss: 0.052 | Acc: 98.438% (16506/16768)
140 391 Loss: 0.052 | Acc: 98.438% (17766/18048)
150 391 Loss: 0.052 | Acc: 98.448% (19028/19328)
160 391 Loss: 0.051 | Acc: 98.481% (20295/20608)
170 391 Loss: 0.052 | Acc: 98.465% (21552/21888)
180 391 Loss: 0.051 | Acc: 98.472% (22814/23168)
190 391 Loss: 0.051 | Acc: 98.487% (24078/24448)
200 391 Loss: 0.051 | Acc: 98.523% (25348/25728)
210 391 Loss: 0.050 | Acc: 98.534% (26612/27008)
220 391 Loss: 0.051 | Acc: 98.505% (27865/28288)
230 391 Loss: 0.051 | Acc: 98.515% (29129/29568)
240 391 Loss: 0.051 | Acc: 98.528% (30394/30848)
250 391 Loss: 0.050 | Acc: 98.543% (31660/32128)
260 391 Loss: 0.050 | Acc: 98.548% (32923/33408)
270 391 Loss: 0.050 | Acc: 98.579% (34195/34688)
280 391 Loss: 0.050 | Acc: 98.593% (35462/35968)
290 391 Loss: 0.050 |

In [17]:
# ResNet20의 best_accuracy dropout 1개
best_accuracy

90.56

## dropout 2개( 2n , 4n 사이 / 4n , 6n사이) opt:Adam

In [31]:
best_accuracy = 0
start_epoch = 0

net = resnet20()
net = net.to(device)
if device == 'cuda':
  net = torch.nn.DataParallel(net)
  cudnn.benchmark = True
    
criterion = nn.CrossEntropyLoss()
#optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
optimizer = optim.Adam(net.parameters(), lr=0.01, weight_decay=1e-4)

#optimizer = optim.SGD(net.parameters(), lr=0.1,momentum=0.9, weight_decay=1e-4)
#decay_epoch = [32000, 48000]
#scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=decay_epoch, gamma=0.1)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
  train(epoch)
  test(epoch)
  scheduler.step()
  print('epoch : ',epoch, best_accuracy)

0 391 Loss: 4.124 | Acc: 8.594% (11/128)
10 391 Loss: 2.939 | Acc: 18.537% (261/1408)
20 391 Loss: 2.560 | Acc: 20.461% (550/2688)
30 391 Loss: 2.383 | Acc: 21.951% (871/3968)
40 391 Loss: 2.274 | Acc: 22.904% (1202/5248)
50 391 Loss: 2.202 | Acc: 23.698% (1547/6528)
60 391 Loss: 2.157 | Acc: 24.206% (1890/7808)
70 391 Loss: 2.116 | Acc: 24.835% (2257/9088)
80 391 Loss: 2.077 | Acc: 25.801% (2675/10368)
90 391 Loss: 2.043 | Acc: 26.580% (3096/11648)
100 391 Loss: 2.007 | Acc: 27.676% (3578/12928)
110 391 Loss: 1.978 | Acc: 28.547% (4056/14208)
120 391 Loss: 1.957 | Acc: 29.081% (4504/15488)
130 391 Loss: 1.936 | Acc: 29.610% (4965/16768)
140 391 Loss: 1.917 | Acc: 30.181% (5447/18048)
150 391 Loss: 1.900 | Acc: 30.795% (5952/19328)
160 391 Loss: 1.890 | Acc: 31.124% (6414/20608)
170 391 Loss: 1.876 | Acc: 31.661% (6930/21888)
180 391 Loss: 1.868 | Acc: 31.967% (7406/23168)
190 391 Loss: 1.857 | Acc: 32.326% (7903/24448)
200 391 Loss: 1.843 | Acc: 32.789% (8436/25728)
210 391 Loss: 1.83

20 391 Loss: 0.901 | Acc: 67.894% (1825/2688)
30 391 Loss: 0.896 | Acc: 68.372% (2713/3968)
40 391 Loss: 0.894 | Acc: 68.769% (3609/5248)
50 391 Loss: 0.892 | Acc: 68.811% (4492/6528)
60 391 Loss: 0.895 | Acc: 68.571% (5354/7808)
70 391 Loss: 0.897 | Acc: 68.398% (6216/9088)
80 391 Loss: 0.897 | Acc: 68.403% (7092/10368)
90 391 Loss: 0.892 | Acc: 68.389% (7966/11648)
100 391 Loss: 0.902 | Acc: 68.031% (8795/12928)
110 391 Loss: 0.901 | Acc: 68.110% (9677/14208)
120 391 Loss: 0.898 | Acc: 68.343% (10585/15488)
130 391 Loss: 0.897 | Acc: 68.285% (11450/16768)
140 391 Loss: 0.901 | Acc: 68.107% (12292/18048)
150 391 Loss: 0.905 | Acc: 68.062% (13155/19328)
160 391 Loss: 0.906 | Acc: 67.983% (14010/20608)
170 391 Loss: 0.902 | Acc: 68.138% (14914/21888)
180 391 Loss: 0.899 | Acc: 68.202% (15801/23168)
190 391 Loss: 0.899 | Acc: 68.145% (16660/24448)
200 391 Loss: 0.900 | Acc: 68.144% (17532/25728)
210 391 Loss: 0.900 | Acc: 68.195% (18418/27008)
220 391 Loss: 0.900 | Acc: 68.174% (19285/28

30 391 Loss: 0.730 | Acc: 74.294% (2948/3968)
40 391 Loss: 0.747 | Acc: 73.704% (3868/5248)
50 391 Loss: 0.753 | Acc: 73.698% (4811/6528)
60 391 Loss: 0.753 | Acc: 73.681% (5753/7808)
70 391 Loss: 0.752 | Acc: 73.647% (6693/9088)
80 391 Loss: 0.753 | Acc: 73.630% (7634/10368)
90 391 Loss: 0.754 | Acc: 73.635% (8577/11648)
100 391 Loss: 0.747 | Acc: 73.933% (9558/12928)
110 391 Loss: 0.743 | Acc: 74.071% (10524/14208)
120 391 Loss: 0.742 | Acc: 74.141% (11483/15488)
130 391 Loss: 0.745 | Acc: 74.082% (12422/16768)
140 391 Loss: 0.744 | Acc: 74.091% (13372/18048)
150 391 Loss: 0.744 | Acc: 74.064% (14315/19328)
160 391 Loss: 0.744 | Acc: 74.015% (15253/20608)
170 391 Loss: 0.748 | Acc: 73.840% (16162/21888)
180 391 Loss: 0.749 | Acc: 73.787% (17095/23168)
190 391 Loss: 0.752 | Acc: 73.802% (18043/24448)
200 391 Loss: 0.753 | Acc: 73.729% (18969/25728)
210 391 Loss: 0.754 | Acc: 73.704% (19906/27008)
220 391 Loss: 0.753 | Acc: 73.749% (20862/28288)
230 391 Loss: 0.754 | Acc: 73.711% (2179

40 391 Loss: 0.693 | Acc: 75.553% (3965/5248)
50 391 Loss: 0.685 | Acc: 75.843% (4951/6528)
60 391 Loss: 0.695 | Acc: 75.730% (5913/7808)
70 391 Loss: 0.696 | Acc: 75.605% (6871/9088)
80 391 Loss: 0.698 | Acc: 75.424% (7820/10368)
90 391 Loss: 0.701 | Acc: 75.395% (8782/11648)
100 391 Loss: 0.705 | Acc: 75.209% (9723/12928)
110 391 Loss: 0.702 | Acc: 75.465% (10722/14208)
120 391 Loss: 0.700 | Acc: 75.517% (11696/15488)
130 391 Loss: 0.701 | Acc: 75.537% (12666/16768)
140 391 Loss: 0.701 | Acc: 75.609% (13646/18048)
150 391 Loss: 0.702 | Acc: 75.621% (14616/19328)
160 391 Loss: 0.701 | Acc: 75.694% (15599/20608)
170 391 Loss: 0.701 | Acc: 75.585% (16544/21888)
180 391 Loss: 0.700 | Acc: 75.652% (17527/23168)
190 391 Loss: 0.700 | Acc: 75.614% (18486/24448)
200 391 Loss: 0.696 | Acc: 75.742% (19487/25728)
210 391 Loss: 0.698 | Acc: 75.711% (20448/27008)
220 391 Loss: 0.699 | Acc: 75.647% (21399/28288)
230 391 Loss: 0.700 | Acc: 75.575% (22346/29568)
240 391 Loss: 0.702 | Acc: 75.506% (2

50 391 Loss: 0.668 | Acc: 77.114% (5034/6528)
60 391 Loss: 0.668 | Acc: 77.113% (6021/7808)
70 391 Loss: 0.671 | Acc: 77.168% (7013/9088)
80 391 Loss: 0.670 | Acc: 77.093% (7993/10368)
90 391 Loss: 0.674 | Acc: 76.863% (8953/11648)
100 391 Loss: 0.674 | Acc: 76.833% (9933/12928)
110 391 Loss: 0.674 | Acc: 76.774% (10908/14208)
120 391 Loss: 0.673 | Acc: 76.860% (11904/15488)
130 391 Loss: 0.675 | Acc: 76.801% (12878/16768)
140 391 Loss: 0.678 | Acc: 76.629% (13830/18048)
150 391 Loss: 0.677 | Acc: 76.656% (14816/19328)
160 391 Loss: 0.678 | Acc: 76.635% (15793/20608)
170 391 Loss: 0.678 | Acc: 76.640% (16775/21888)
180 391 Loss: 0.677 | Acc: 76.675% (17764/23168)
190 391 Loss: 0.676 | Acc: 76.693% (18750/24448)
200 391 Loss: 0.677 | Acc: 76.714% (19737/25728)
210 391 Loss: 0.676 | Acc: 76.762% (20732/27008)
220 391 Loss: 0.676 | Acc: 76.775% (21718/28288)
230 391 Loss: 0.675 | Acc: 76.786% (22704/29568)
240 391 Loss: 0.676 | Acc: 76.754% (23677/30848)
250 391 Loss: 0.675 | Acc: 76.774%

...

200 391 Loss: 0.247 | Acc: 91.647% (23579/25728)
210 391 Loss: 0.247 | Acc: 91.658% (24755/27008)
220 391 Loss: 0.247 | Acc: 91.625% (25919/28288)
230 391 Loss: 0.246 | Acc: 91.646% (27098/29568)
240 391 Loss: 0.245 | Acc: 91.653% (28273/30848)
250 391 Loss: 0.245 | Acc: 91.655% (29447/32128)
260 391 Loss: 0.246 | Acc: 91.631% (30612/33408)
270 391 Loss: 0.246 | Acc: 91.628% (31784/34688)
280 391 Loss: 0.246 | Acc: 91.606% (32949/35968)
290 391 Loss: 0.247 | Acc: 91.562% (34105/37248)
300 391 Loss: 0.246 | Acc: 91.572% (35281/38528)
310 391 Loss: 0.245 | Acc: 91.572% (36453/39808)
320 391 Loss: 0.247 | Acc: 91.533% (37609/41088)
330 391 Loss: 0.247 | Acc: 91.531% (38780/42368)
340 391 Loss: 0.247 | Acc: 91.528% (39950/43648)
350 391 Loss: 0.246 | Acc: 91.522% (41119/44928)
360 391 Loss: 0.246 | Acc: 91.534% (42296/46208)
370 391 Loss: 0.246 | Acc: 91.514% (43458/47488)
380 391 Loss: 0.247 | Acc: 91.488% (44617/48768)
390 391 Loss: 0.247 | Acc: 91.474% (45737/50000)
0 100 Loss: 0.232 | 

210 391 Loss: 0.240 | Acc: 91.573% (24732/27008)
220 391 Loss: 0.240 | Acc: 91.576% (25905/28288)
230 391 Loss: 0.239 | Acc: 91.609% (27087/29568)
240 391 Loss: 0.240 | Acc: 91.552% (28242/30848)
250 391 Loss: 0.240 | Acc: 91.574% (29421/32128)
260 391 Loss: 0.240 | Acc: 91.547% (30584/33408)
270 391 Loss: 0.241 | Acc: 91.533% (31751/34688)
280 391 Loss: 0.240 | Acc: 91.506% (32913/35968)
290 391 Loss: 0.240 | Acc: 91.500% (34082/37248)
300 391 Loss: 0.240 | Acc: 91.497% (35252/38528)
310 391 Loss: 0.239 | Acc: 91.484% (36418/39808)
320 391 Loss: 0.239 | Acc: 91.482% (37588/41088)
330 391 Loss: 0.239 | Acc: 91.484% (38760/42368)
340 391 Loss: 0.240 | Acc: 91.493% (39935/43648)
350 391 Loss: 0.240 | Acc: 91.495% (41107/44928)
360 391 Loss: 0.239 | Acc: 91.540% (42299/46208)
370 391 Loss: 0.240 | Acc: 91.518% (43460/47488)
380 391 Loss: 0.241 | Acc: 91.531% (44638/48768)
390 391 Loss: 0.240 | Acc: 91.578% (45789/50000)
0 100 Loss: 0.224 | Acc: 93.000% (93/100)
50 100 Loss: 0.329 | Acc: 8

220 391 Loss: 0.235 | Acc: 91.739% (25951/28288)
230 391 Loss: 0.233 | Acc: 91.785% (27139/29568)
240 391 Loss: 0.233 | Acc: 91.808% (28321/30848)
250 391 Loss: 0.233 | Acc: 91.817% (29499/32128)
260 391 Loss: 0.232 | Acc: 91.807% (30671/33408)
270 391 Loss: 0.232 | Acc: 91.824% (31852/34688)
280 391 Loss: 0.233 | Acc: 91.823% (33027/35968)
290 391 Loss: 0.233 | Acc: 91.836% (34207/37248)
300 391 Loss: 0.234 | Acc: 91.777% (35360/38528)
310 391 Loss: 0.233 | Acc: 91.798% (36543/39808)
320 391 Loss: 0.233 | Acc: 91.779% (37710/41088)
330 391 Loss: 0.232 | Acc: 91.803% (38895/42368)
340 391 Loss: 0.233 | Acc: 91.789% (40064/43648)
350 391 Loss: 0.233 | Acc: 91.791% (41240/44928)
360 391 Loss: 0.234 | Acc: 91.776% (42408/46208)
370 391 Loss: 0.233 | Acc: 91.781% (43585/47488)
380 391 Loss: 0.234 | Acc: 91.769% (44754/48768)
390 391 Loss: 0.236 | Acc: 91.724% (45862/50000)
0 100 Loss: 0.231 | Acc: 93.000% (93/100)
50 100 Loss: 0.334 | Acc: 89.510% (4565/5100)
epoch :  189 89.64
0 391 Loss:

230 391 Loss: 0.227 | Acc: 92.062% (27221/29568)
240 391 Loss: 0.227 | Acc: 92.045% (28394/30848)
250 391 Loss: 0.226 | Acc: 92.066% (29579/32128)
260 391 Loss: 0.227 | Acc: 92.050% (30752/33408)
270 391 Loss: 0.226 | Acc: 92.095% (31946/34688)
280 391 Loss: 0.227 | Acc: 92.051% (33109/35968)
290 391 Loss: 0.227 | Acc: 92.024% (34277/37248)
300 391 Loss: 0.228 | Acc: 91.998% (35445/38528)
310 391 Loss: 0.228 | Acc: 92.032% (36636/39808)
320 391 Loss: 0.229 | Acc: 91.983% (37794/41088)
330 391 Loss: 0.229 | Acc: 91.987% (38973/42368)
340 391 Loss: 0.228 | Acc: 92.025% (40167/43648)
350 391 Loss: 0.228 | Acc: 92.001% (41334/44928)
360 391 Loss: 0.228 | Acc: 92.004% (42513/46208)
370 391 Loss: 0.228 | Acc: 91.990% (43684/47488)
380 391 Loss: 0.228 | Acc: 92.017% (44875/48768)
390 391 Loss: 0.228 | Acc: 92.038% (46019/50000)
0 100 Loss: 0.238 | Acc: 92.000% (92/100)
50 100 Loss: 0.331 | Acc: 89.549% (4567/5100)
epoch :  193 89.64
0 391 Loss: 0.158 | Acc: 96.094% (123/128)
10 391 Loss: 0.19

240 391 Loss: 0.234 | Acc: 91.769% (28309/30848)
250 391 Loss: 0.233 | Acc: 91.792% (29491/32128)
260 391 Loss: 0.232 | Acc: 91.837% (30681/33408)
270 391 Loss: 0.233 | Acc: 91.824% (31852/34688)
280 391 Loss: 0.233 | Acc: 91.829% (33029/35968)
290 391 Loss: 0.233 | Acc: 91.812% (34198/37248)
300 391 Loss: 0.232 | Acc: 91.866% (35394/38528)
310 391 Loss: 0.232 | Acc: 91.871% (36572/39808)
320 391 Loss: 0.231 | Acc: 91.917% (37767/41088)
330 391 Loss: 0.232 | Acc: 91.907% (38939/42368)
340 391 Loss: 0.232 | Acc: 91.867% (40098/43648)
350 391 Loss: 0.232 | Acc: 91.880% (41280/44928)
360 391 Loss: 0.232 | Acc: 91.904% (42467/46208)
370 391 Loss: 0.231 | Acc: 91.928% (43655/47488)
380 391 Loss: 0.230 | Acc: 91.956% (44845/48768)
390 391 Loss: 0.230 | Acc: 91.960% (45980/50000)
0 100 Loss: 0.229 | Acc: 92.000% (92/100)
50 100 Loss: 0.335 | Acc: 89.608% (4570/5100)
epoch :  197 89.64
0 391 Loss: 0.189 | Acc: 92.969% (119/128)
10 391 Loss: 0.235 | Acc: 92.045% (1296/1408)
20 391 Loss: 0.241 |

In [32]:
# ResNet20의 best_accuracy dropout 2개( 1 , 2n 사이 / 2n , 4n 사이) opt:Adam
best_accuracy

89.75

## dropout 2개( 2n , 4n 사이 / 4n , 6n사이) opt : sgd

In [33]:
best_accuracy = 0
start_epoch = 0

net = resnet20()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True
    
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
#optimizer = optim.Adam(net.parameters(), lr=0.01, weight_decay=1e-4)

#optimizer = optim.SGD(net.parameters(), lr=0.1,momentum=0.9, weight_decay=1e-4)
#decay_epoch = [32000, 48000]
#scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=decay_epoch, gamma=0.1)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 3.162 | Acc: 10.156% (13/128)
10 391 Loss: 2.589 | Acc: 11.861% (167/1408)
20 391 Loss: 2.433 | Acc: 14.286% (384/2688)
30 391 Loss: 2.329 | Acc: 16.709% (663/3968)
40 391 Loss: 2.255 | Acc: 18.293% (960/5248)
50 391 Loss: 2.205 | Acc: 19.746% (1289/6528)
60 391 Loss: 2.157 | Acc: 21.363% (1668/7808)
70 391 Loss: 2.118 | Acc: 22.161% (2014/9088)
80 391 Loss: 2.086 | Acc: 23.187% (2404/10368)
90 391 Loss: 2.056 | Acc: 24.013% (2797/11648)
100 391 Loss: 2.032 | Acc: 24.799% (3206/12928)
110 391 Loss: 2.013 | Acc: 25.493% (3622/14208)
120 391 Loss: 1.997 | Acc: 25.943% (4018/15488)
130 391 Loss: 1.979 | Acc: 26.491% (4442/16768)
140 391 Loss: 1.967 | Acc: 26.801% (4837/18048)
150 391 Loss: 1.954 | Acc: 27.157% (5249/19328)
160 391 Loss: 1.942 | Acc: 27.654% (5699/20608)
170 391 Loss: 1.932 | Acc: 28.006% (6130/21888)
180 391 Loss: 1.921 | Acc: 28.423% (6585/23168)
190 391 Loss: 1.910 | Acc: 28.837% (7050/24448)
200 391 Loss: 1.899 | Acc: 29.171% (7505/25728)
210 391 Loss: 1.89

20 391 Loss: 1.106 | Acc: 59.821% (1608/2688)
30 391 Loss: 1.109 | Acc: 60.005% (2381/3968)
40 391 Loss: 1.115 | Acc: 60.061% (3152/5248)
50 391 Loss: 1.112 | Acc: 60.539% (3952/6528)
60 391 Loss: 1.111 | Acc: 60.182% (4699/7808)
70 391 Loss: 1.104 | Acc: 60.442% (5493/9088)
80 391 Loss: 1.103 | Acc: 60.581% (6281/10368)
90 391 Loss: 1.102 | Acc: 60.637% (7063/11648)
100 391 Loss: 1.104 | Acc: 60.651% (7841/12928)
110 391 Loss: 1.101 | Acc: 60.740% (8630/14208)
120 391 Loss: 1.099 | Acc: 60.821% (9420/15488)
130 391 Loss: 1.098 | Acc: 60.878% (10208/16768)
140 391 Loss: 1.097 | Acc: 60.965% (11003/18048)
150 391 Loss: 1.101 | Acc: 60.793% (11750/19328)
160 391 Loss: 1.100 | Acc: 60.729% (12515/20608)
170 391 Loss: 1.094 | Acc: 60.915% (13333/21888)
180 391 Loss: 1.094 | Acc: 60.881% (14105/23168)
190 391 Loss: 1.091 | Acc: 61.052% (14926/24448)
200 391 Loss: 1.088 | Acc: 61.105% (15721/25728)
210 391 Loss: 1.087 | Acc: 61.163% (16519/27008)
220 391 Loss: 1.085 | Acc: 61.234% (17322/282

40 391 Loss: 0.880 | Acc: 68.559% (3598/5248)
50 391 Loss: 0.887 | Acc: 68.321% (4460/6528)
60 391 Loss: 0.885 | Acc: 68.417% (5342/7808)
70 391 Loss: 0.893 | Acc: 68.145% (6193/9088)
80 391 Loss: 0.894 | Acc: 68.268% (7078/10368)
90 391 Loss: 0.894 | Acc: 68.235% (7948/11648)
100 391 Loss: 0.897 | Acc: 68.170% (8813/12928)
110 391 Loss: 0.889 | Acc: 68.433% (9723/14208)
120 391 Loss: 0.890 | Acc: 68.324% (10582/15488)
130 391 Loss: 0.889 | Acc: 68.297% (11452/16768)
140 391 Loss: 0.887 | Acc: 68.423% (12349/18048)
150 391 Loss: 0.887 | Acc: 68.424% (13225/19328)
160 391 Loss: 0.886 | Acc: 68.405% (14097/20608)
170 391 Loss: 0.884 | Acc: 68.453% (14983/21888)
180 391 Loss: 0.884 | Acc: 68.560% (15884/23168)
190 391 Loss: 0.885 | Acc: 68.472% (16740/24448)
200 391 Loss: 0.884 | Acc: 68.560% (17639/25728)
210 391 Loss: 0.883 | Acc: 68.620% (18533/27008)
220 391 Loss: 0.882 | Acc: 68.672% (19426/28288)
230 391 Loss: 0.883 | Acc: 68.598% (20283/29568)
240 391 Loss: 0.883 | Acc: 68.669% (21

50 391 Loss: 0.743 | Acc: 74.219% (4845/6528)
60 391 Loss: 0.747 | Acc: 74.129% (5788/7808)
70 391 Loss: 0.744 | Acc: 74.120% (6736/9088)
80 391 Loss: 0.743 | Acc: 74.007% (7673/10368)
90 391 Loss: 0.742 | Acc: 73.987% (8618/11648)
100 391 Loss: 0.744 | Acc: 73.902% (9554/12928)
110 391 Loss: 0.747 | Acc: 73.663% (10466/14208)
120 391 Loss: 0.752 | Acc: 73.502% (11384/15488)
130 391 Loss: 0.754 | Acc: 73.497% (12324/16768)
140 391 Loss: 0.756 | Acc: 73.393% (13246/18048)
150 391 Loss: 0.753 | Acc: 73.500% (14206/19328)
160 391 Loss: 0.752 | Acc: 73.578% (15163/20608)
170 391 Loss: 0.753 | Acc: 73.501% (16088/21888)
180 391 Loss: 0.754 | Acc: 73.368% (16998/23168)
190 391 Loss: 0.753 | Acc: 73.442% (17955/24448)
200 391 Loss: 0.751 | Acc: 73.469% (18902/25728)
210 391 Loss: 0.751 | Acc: 73.471% (19843/27008)
220 391 Loss: 0.750 | Acc: 73.508% (20794/28288)
230 391 Loss: 0.750 | Acc: 73.509% (21735/29568)
240 391 Loss: 0.749 | Acc: 73.509% (22676/30848)
250 391 Loss: 0.748 | Acc: 73.578%

60 391 Loss: 0.652 | Acc: 77.331% (6038/7808)
70 391 Loss: 0.655 | Acc: 77.278% (7023/9088)
80 391 Loss: 0.656 | Acc: 77.353% (8020/10368)
90 391 Loss: 0.658 | Acc: 77.318% (9006/11648)
100 391 Loss: 0.656 | Acc: 77.444% (10012/12928)
110 391 Loss: 0.655 | Acc: 77.477% (11008/14208)
120 391 Loss: 0.659 | Acc: 77.318% (11975/15488)
130 391 Loss: 0.658 | Acc: 77.314% (12964/16768)
140 391 Loss: 0.660 | Acc: 77.311% (13953/18048)
150 391 Loss: 0.657 | Acc: 77.483% (14976/19328)
160 391 Loss: 0.658 | Acc: 77.446% (15960/20608)
170 391 Loss: 0.657 | Acc: 77.472% (16957/21888)
180 391 Loss: 0.654 | Acc: 77.538% (17964/23168)
190 391 Loss: 0.657 | Acc: 77.454% (18936/24448)
200 391 Loss: 0.655 | Acc: 77.491% (19937/25728)
210 391 Loss: 0.656 | Acc: 77.418% (20909/27008)
220 391 Loss: 0.655 | Acc: 77.453% (21910/28288)
230 391 Loss: 0.657 | Acc: 77.388% (22882/29568)
240 391 Loss: 0.658 | Acc: 77.328% (23854/30848)
250 391 Loss: 0.659 | Acc: 77.310% (24838/32128)
260 391 Loss: 0.662 | Acc: 77.

...

60 391 Loss: 0.087 | Acc: 97.144% (7585/7808)
70 391 Loss: 0.088 | Acc: 97.128% (8827/9088)
80 391 Loss: 0.088 | Acc: 97.174% (10075/10368)
90 391 Loss: 0.088 | Acc: 97.141% (11315/11648)
100 391 Loss: 0.088 | Acc: 97.153% (12560/12928)
110 391 Loss: 0.087 | Acc: 97.206% (13811/14208)
120 391 Loss: 0.087 | Acc: 97.230% (15059/15488)
130 391 Loss: 0.087 | Acc: 97.269% (16310/16768)
140 391 Loss: 0.087 | Acc: 97.196% (17542/18048)
150 391 Loss: 0.087 | Acc: 97.185% (18784/19328)
160 391 Loss: 0.087 | Acc: 97.205% (20032/20608)
170 391 Loss: 0.088 | Acc: 97.177% (21270/21888)
180 391 Loss: 0.088 | Acc: 97.156% (22509/23168)
190 391 Loss: 0.087 | Acc: 97.145% (23750/24448)
200 391 Loss: 0.089 | Acc: 97.104% (24983/25728)
210 391 Loss: 0.088 | Acc: 97.145% (26237/27008)
220 391 Loss: 0.088 | Acc: 97.151% (27482/28288)
230 391 Loss: 0.087 | Acc: 97.142% (28723/29568)
240 391 Loss: 0.087 | Acc: 97.157% (29971/30848)
250 391 Loss: 0.088 | Acc: 97.140% (31209/32128)
260 391 Loss: 0.087 | Acc: 9

70 391 Loss: 0.086 | Acc: 97.216% (8835/9088)
80 391 Loss: 0.084 | Acc: 97.319% (10090/10368)
90 391 Loss: 0.085 | Acc: 97.313% (11335/11648)
100 391 Loss: 0.086 | Acc: 97.239% (12571/12928)
110 391 Loss: 0.085 | Acc: 97.276% (13821/14208)
120 391 Loss: 0.084 | Acc: 97.308% (15071/15488)
130 391 Loss: 0.084 | Acc: 97.316% (16318/16768)
140 391 Loss: 0.085 | Acc: 97.285% (17558/18048)
150 391 Loss: 0.085 | Acc: 97.268% (18800/19328)
160 391 Loss: 0.085 | Acc: 97.283% (20048/20608)
170 391 Loss: 0.085 | Acc: 97.282% (21293/21888)
180 391 Loss: 0.086 | Acc: 97.289% (22540/23168)
190 391 Loss: 0.085 | Acc: 97.288% (23785/24448)
200 391 Loss: 0.085 | Acc: 97.326% (25040/25728)
210 391 Loss: 0.085 | Acc: 97.323% (26285/27008)
220 391 Loss: 0.085 | Acc: 97.349% (27538/28288)
230 391 Loss: 0.085 | Acc: 97.335% (28780/29568)
240 391 Loss: 0.085 | Acc: 97.313% (30019/30848)
250 391 Loss: 0.086 | Acc: 97.280% (31254/32128)
260 391 Loss: 0.086 | Acc: 97.246% (32488/33408)
270 391 Loss: 0.087 | Acc

80 391 Loss: 0.084 | Acc: 97.242% (10082/10368)
90 391 Loss: 0.084 | Acc: 97.244% (11327/11648)
100 391 Loss: 0.083 | Acc: 97.355% (12586/12928)
110 391 Loss: 0.083 | Acc: 97.311% (13826/14208)
120 391 Loss: 0.084 | Acc: 97.249% (15062/15488)
130 391 Loss: 0.084 | Acc: 97.269% (16310/16768)
140 391 Loss: 0.083 | Acc: 97.296% (17560/18048)
150 391 Loss: 0.082 | Acc: 97.346% (18815/19328)
160 391 Loss: 0.082 | Acc: 97.355% (20063/20608)
170 391 Loss: 0.082 | Acc: 97.364% (21311/21888)
180 391 Loss: 0.082 | Acc: 97.376% (22560/23168)
190 391 Loss: 0.082 | Acc: 97.370% (23805/24448)
200 391 Loss: 0.082 | Acc: 97.376% (25053/25728)
210 391 Loss: 0.082 | Acc: 97.386% (26302/27008)
220 391 Loss: 0.082 | Acc: 97.373% (27545/28288)
230 391 Loss: 0.082 | Acc: 97.399% (28799/29568)
240 391 Loss: 0.083 | Acc: 97.348% (30030/30848)
250 391 Loss: 0.083 | Acc: 97.364% (31281/32128)
260 391 Loss: 0.083 | Acc: 97.363% (32527/33408)
270 391 Loss: 0.083 | Acc: 97.359% (33772/34688)
280 391 Loss: 0.083 | 

90 391 Loss: 0.084 | Acc: 97.390% (11344/11648)
100 391 Loss: 0.083 | Acc: 97.424% (12595/12928)
110 391 Loss: 0.083 | Acc: 97.452% (13846/14208)
120 391 Loss: 0.083 | Acc: 97.475% (15097/15488)
130 391 Loss: 0.084 | Acc: 97.459% (16342/16768)
140 391 Loss: 0.084 | Acc: 97.435% (17585/18048)
150 391 Loss: 0.085 | Acc: 97.423% (18830/19328)
160 391 Loss: 0.084 | Acc: 97.414% (20075/20608)
170 391 Loss: 0.084 | Acc: 97.432% (21326/21888)
180 391 Loss: 0.084 | Acc: 97.445% (22576/23168)
190 391 Loss: 0.084 | Acc: 97.460% (23827/24448)
200 391 Loss: 0.084 | Acc: 97.485% (25081/25728)
210 391 Loss: 0.083 | Acc: 97.501% (26333/27008)
220 391 Loss: 0.083 | Acc: 97.494% (27579/28288)
230 391 Loss: 0.084 | Acc: 97.460% (28817/29568)
240 391 Loss: 0.083 | Acc: 97.471% (30068/30848)
250 391 Loss: 0.082 | Acc: 97.479% (31318/32128)
260 391 Loss: 0.082 | Acc: 97.471% (32563/33408)
270 391 Loss: 0.083 | Acc: 97.466% (33809/34688)
280 391 Loss: 0.083 | Acc: 97.448% (35050/35968)
290 391 Loss: 0.083 |

100 391 Loss: 0.084 | Acc: 97.316% (12581/12928)
110 391 Loss: 0.085 | Acc: 97.304% (13825/14208)
120 391 Loss: 0.086 | Acc: 97.282% (15067/15488)
130 391 Loss: 0.086 | Acc: 97.263% (16309/16768)
140 391 Loss: 0.085 | Acc: 97.318% (17564/18048)
150 391 Loss: 0.086 | Acc: 97.310% (18808/19328)
160 391 Loss: 0.085 | Acc: 97.312% (20054/20608)
170 391 Loss: 0.086 | Acc: 97.291% (21295/21888)
180 391 Loss: 0.085 | Acc: 97.311% (22545/23168)
190 391 Loss: 0.085 | Acc: 97.345% (23799/24448)
200 391 Loss: 0.084 | Acc: 97.361% (25049/25728)
210 391 Loss: 0.084 | Acc: 97.360% (26295/27008)
220 391 Loss: 0.084 | Acc: 97.370% (27544/28288)
230 391 Loss: 0.084 | Acc: 97.338% (28781/29568)
240 391 Loss: 0.083 | Acc: 97.345% (30029/30848)
250 391 Loss: 0.083 | Acc: 97.367% (31282/32128)
260 391 Loss: 0.083 | Acc: 97.372% (32530/33408)
270 391 Loss: 0.083 | Acc: 97.365% (33774/34688)
280 391 Loss: 0.083 | Acc: 97.384% (35027/35968)
290 391 Loss: 0.083 | Acc: 97.377% (36271/37248)
300 391 Loss: 0.083 

In [34]:
# ResNet20의 best_accuracy dropout 2개( 1 , 2n 사이 / 2n , 4n 사이) opt : sgd
best_accuracy

91.1

In [35]:
best_accuracy = 0
start_epoch = 0
net = resnet32()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True

In [36]:
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)


In [37]:
for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()

0 391 Loss: 5.823 | Acc: 8.594% (11/128)
10 391 Loss: 3.691 | Acc: 10.724% (151/1408)
20 391 Loss: 3.238 | Acc: 11.682% (314/2688)
30 391 Loss: 2.943 | Acc: 12.828% (509/3968)
40 391 Loss: 2.753 | Acc: 14.139% (742/5248)
50 391 Loss: 2.621 | Acc: 15.380% (1004/6528)
60 391 Loss: 2.520 | Acc: 16.816% (1313/7808)
70 391 Loss: 2.443 | Acc: 18.178% (1652/9088)
80 391 Loss: 2.378 | Acc: 19.088% (1979/10368)
90 391 Loss: 2.324 | Acc: 19.978% (2327/11648)
100 391 Loss: 2.274 | Acc: 20.885% (2700/12928)
110 391 Loss: 2.230 | Acc: 21.889% (3110/14208)
120 391 Loss: 2.195 | Acc: 22.637% (3506/15488)
130 391 Loss: 2.163 | Acc: 23.420% (3927/16768)
140 391 Loss: 2.137 | Acc: 23.864% (4307/18048)
150 391 Loss: 2.111 | Acc: 24.415% (4719/19328)
160 391 Loss: 2.088 | Acc: 25.000% (5152/20608)
170 391 Loss: 2.066 | Acc: 25.507% (5583/21888)
180 391 Loss: 2.047 | Acc: 25.924% (6006/23168)
190 391 Loss: 2.029 | Acc: 26.522% (6484/24448)
200 391 Loss: 2.013 | Acc: 26.967% (6938/25728)
210 391 Loss: 1.997

40 391 Loss: 1.104 | Acc: 60.118% (3155/5248)
50 391 Loss: 1.107 | Acc: 60.141% (3926/6528)
60 391 Loss: 1.102 | Acc: 60.348% (4712/7808)
70 391 Loss: 1.100 | Acc: 60.156% (5467/9088)
80 391 Loss: 1.100 | Acc: 60.156% (6237/10368)
90 391 Loss: 1.092 | Acc: 60.397% (7035/11648)
100 391 Loss: 1.087 | Acc: 60.528% (7825/12928)
110 391 Loss: 1.083 | Acc: 60.712% (8626/14208)
120 391 Loss: 1.083 | Acc: 60.802% (9417/15488)
130 391 Loss: 1.080 | Acc: 60.896% (10211/16768)
140 391 Loss: 1.078 | Acc: 61.015% (11012/18048)
150 391 Loss: 1.076 | Acc: 61.005% (11791/19328)
160 391 Loss: 1.078 | Acc: 60.845% (12539/20608)
170 391 Loss: 1.081 | Acc: 60.741% (13295/21888)
180 391 Loss: 1.079 | Acc: 60.894% (14108/23168)
190 391 Loss: 1.079 | Acc: 60.905% (14890/24448)
200 391 Loss: 1.077 | Acc: 60.914% (15672/25728)
210 391 Loss: 1.076 | Acc: 60.860% (16437/27008)
220 391 Loss: 1.076 | Acc: 60.906% (17229/28288)
230 391 Loss: 1.078 | Acc: 60.823% (17984/29568)
240 391 Loss: 1.076 | Acc: 60.886% (187

70 391 Loss: 0.876 | Acc: 69.300% (6298/9088)
80 391 Loss: 0.871 | Acc: 69.387% (7194/10368)
90 391 Loss: 0.865 | Acc: 69.480% (8093/11648)
100 391 Loss: 0.871 | Acc: 69.230% (8950/12928)
110 391 Loss: 0.873 | Acc: 69.032% (9808/14208)
120 391 Loss: 0.876 | Acc: 68.756% (10649/15488)
130 391 Loss: 0.876 | Acc: 68.708% (11521/16768)
140 391 Loss: 0.874 | Acc: 68.744% (12407/18048)
150 391 Loss: 0.871 | Acc: 68.864% (13310/19328)
160 391 Loss: 0.872 | Acc: 68.818% (14182/20608)
170 391 Loss: 0.870 | Acc: 68.846% (15069/21888)
180 391 Loss: 0.868 | Acc: 69.018% (15990/23168)
190 391 Loss: 0.865 | Acc: 69.130% (16901/24448)
200 391 Loss: 0.866 | Acc: 69.123% (17784/25728)
210 391 Loss: 0.865 | Acc: 69.183% (18685/27008)
220 391 Loss: 0.864 | Acc: 69.206% (19577/28288)
230 391 Loss: 0.866 | Acc: 69.139% (20443/29568)
240 391 Loss: 0.865 | Acc: 69.188% (21343/30848)
250 391 Loss: 0.864 | Acc: 69.201% (22233/32128)
260 391 Loss: 0.864 | Acc: 69.151% (23102/33408)
270 391 Loss: 0.861 | Acc: 69

100 391 Loss: 0.722 | Acc: 74.118% (9582/12928)
110 391 Loss: 0.723 | Acc: 74.254% (10550/14208)
120 391 Loss: 0.721 | Acc: 74.509% (11540/15488)
130 391 Loss: 0.724 | Acc: 74.511% (12494/16768)
140 391 Loss: 0.725 | Acc: 74.529% (13451/18048)
150 391 Loss: 0.725 | Acc: 74.555% (14410/19328)
160 391 Loss: 0.725 | Acc: 74.617% (15377/20608)
170 391 Loss: 0.725 | Acc: 74.566% (16321/21888)
180 391 Loss: 0.726 | Acc: 74.594% (17282/23168)
190 391 Loss: 0.727 | Acc: 74.521% (18219/24448)
200 391 Loss: 0.728 | Acc: 74.417% (19146/25728)
210 391 Loss: 0.726 | Acc: 74.467% (20112/27008)
220 391 Loss: 0.723 | Acc: 74.586% (21099/28288)
230 391 Loss: 0.722 | Acc: 74.679% (22081/29568)
240 391 Loss: 0.720 | Acc: 74.750% (23059/30848)
250 391 Loss: 0.720 | Acc: 74.739% (24012/32128)
260 391 Loss: 0.718 | Acc: 74.835% (25001/33408)
270 391 Loss: 0.718 | Acc: 74.839% (25960/34688)
280 391 Loss: 0.719 | Acc: 74.825% (26913/35968)
290 391 Loss: 0.717 | Acc: 74.887% (27894/37248)
300 391 Loss: 0.717 |

130 391 Loss: 0.626 | Acc: 78.125% (13100/16768)
140 391 Loss: 0.625 | Acc: 78.153% (14105/18048)
150 391 Loss: 0.620 | Acc: 78.316% (15137/19328)
160 391 Loss: 0.622 | Acc: 78.251% (16126/20608)
170 391 Loss: 0.623 | Acc: 78.244% (17126/21888)
180 391 Loss: 0.621 | Acc: 78.315% (18144/23168)
190 391 Loss: 0.620 | Acc: 78.325% (19149/24448)
200 391 Loss: 0.618 | Acc: 78.393% (20169/25728)
210 391 Loss: 0.617 | Acc: 78.443% (21186/27008)
220 391 Loss: 0.618 | Acc: 78.454% (22193/28288)
230 391 Loss: 0.618 | Acc: 78.467% (23201/29568)
240 391 Loss: 0.618 | Acc: 78.478% (24209/30848)
250 391 Loss: 0.618 | Acc: 78.474% (25212/32128)
260 391 Loss: 0.619 | Acc: 78.457% (26211/33408)
270 391 Loss: 0.617 | Acc: 78.497% (27229/34688)
280 391 Loss: 0.618 | Acc: 78.464% (28222/35968)
290 391 Loss: 0.619 | Acc: 78.420% (29210/37248)
300 391 Loss: 0.620 | Acc: 78.408% (30209/38528)
310 391 Loss: 0.620 | Acc: 78.381% (31202/39808)
320 391 Loss: 0.619 | Acc: 78.402% (32214/41088)
330 391 Loss: 0.620 

...

90 391 Loss: 0.037 | Acc: 98.884% (11518/11648)
100 391 Loss: 0.038 | Acc: 98.847% (12779/12928)
110 391 Loss: 0.038 | Acc: 98.839% (14043/14208)
120 391 Loss: 0.038 | Acc: 98.838% (15308/15488)
130 391 Loss: 0.038 | Acc: 98.837% (16573/16768)
140 391 Loss: 0.037 | Acc: 98.853% (17841/18048)
150 391 Loss: 0.038 | Acc: 98.851% (19106/19328)
160 391 Loss: 0.038 | Acc: 98.860% (20373/20608)
170 391 Loss: 0.038 | Acc: 98.849% (21636/21888)
180 391 Loss: 0.038 | Acc: 98.865% (22905/23168)
190 391 Loss: 0.038 | Acc: 98.859% (24169/24448)
200 391 Loss: 0.037 | Acc: 98.892% (25443/25728)
210 391 Loss: 0.038 | Acc: 98.889% (26708/27008)
220 391 Loss: 0.038 | Acc: 98.897% (27976/28288)
230 391 Loss: 0.038 | Acc: 98.887% (29239/29568)
240 391 Loss: 0.038 | Acc: 98.885% (30504/30848)
250 391 Loss: 0.038 | Acc: 98.886% (31770/32128)
260 391 Loss: 0.038 | Acc: 98.884% (33035/33408)
270 391 Loss: 0.038 | Acc: 98.890% (34303/34688)
280 391 Loss: 0.038 | Acc: 98.885% (35567/35968)
290 391 Loss: 0.038 |

120 391 Loss: 0.038 | Acc: 98.922% (15321/15488)
130 391 Loss: 0.038 | Acc: 98.927% (16588/16768)
140 391 Loss: 0.038 | Acc: 98.897% (17849/18048)
150 391 Loss: 0.038 | Acc: 98.924% (19120/19328)
160 391 Loss: 0.037 | Acc: 98.928% (20387/20608)
170 391 Loss: 0.037 | Acc: 98.926% (21653/21888)
180 391 Loss: 0.037 | Acc: 98.904% (22914/23168)
190 391 Loss: 0.038 | Acc: 98.916% (24183/24448)
200 391 Loss: 0.037 | Acc: 98.927% (25452/25728)
210 391 Loss: 0.037 | Acc: 98.915% (26715/27008)
220 391 Loss: 0.037 | Acc: 98.925% (27984/28288)
230 391 Loss: 0.037 | Acc: 98.921% (29249/29568)
240 391 Loss: 0.037 | Acc: 98.930% (30518/30848)
250 391 Loss: 0.037 | Acc: 98.932% (31785/32128)
260 391 Loss: 0.037 | Acc: 98.946% (33056/33408)
270 391 Loss: 0.037 | Acc: 98.942% (34321/34688)
280 391 Loss: 0.037 | Acc: 98.944% (35588/35968)
290 391 Loss: 0.037 | Acc: 98.931% (36850/37248)
300 391 Loss: 0.037 | Acc: 98.936% (38118/38528)
310 391 Loss: 0.037 | Acc: 98.937% (39385/39808)
320 391 Loss: 0.037 

150 391 Loss: 0.035 | Acc: 99.012% (19137/19328)
160 391 Loss: 0.035 | Acc: 99.015% (20405/20608)
170 391 Loss: 0.035 | Acc: 99.009% (21671/21888)
180 391 Loss: 0.035 | Acc: 98.986% (22933/23168)
190 391 Loss: 0.035 | Acc: 98.965% (24195/24448)
200 391 Loss: 0.035 | Acc: 98.974% (25464/25728)
210 391 Loss: 0.035 | Acc: 98.971% (26730/27008)
220 391 Loss: 0.035 | Acc: 98.964% (27995/28288)
230 391 Loss: 0.035 | Acc: 98.989% (29269/29568)
240 391 Loss: 0.035 | Acc: 98.976% (30532/30848)
250 391 Loss: 0.035 | Acc: 98.967% (31796/32128)
260 391 Loss: 0.036 | Acc: 98.958% (33060/33408)
270 391 Loss: 0.036 | Acc: 98.956% (34326/34688)
280 391 Loss: 0.036 | Acc: 98.969% (35597/35968)
290 391 Loss: 0.036 | Acc: 98.972% (36865/37248)
300 391 Loss: 0.035 | Acc: 98.970% (38131/38528)
310 391 Loss: 0.036 | Acc: 98.963% (39395/39808)
320 391 Loss: 0.036 | Acc: 98.968% (40664/41088)
330 391 Loss: 0.036 | Acc: 98.969% (41931/42368)
340 391 Loss: 0.036 | Acc: 98.967% (43197/43648)
350 391 Loss: 0.035 

180 391 Loss: 0.034 | Acc: 99.046% (22947/23168)
190 391 Loss: 0.034 | Acc: 99.051% (24216/24448)
200 391 Loss: 0.034 | Acc: 99.044% (25482/25728)
210 391 Loss: 0.034 | Acc: 99.037% (26748/27008)
220 391 Loss: 0.034 | Acc: 99.028% (28013/28288)
230 391 Loss: 0.034 | Acc: 99.036% (29283/29568)
240 391 Loss: 0.034 | Acc: 99.031% (30549/30848)
250 391 Loss: 0.034 | Acc: 99.023% (31814/32128)
260 391 Loss: 0.034 | Acc: 99.024% (33082/33408)
270 391 Loss: 0.034 | Acc: 99.011% (34345/34688)
280 391 Loss: 0.034 | Acc: 99.007% (35611/35968)
290 391 Loss: 0.035 | Acc: 98.996% (36874/37248)
300 391 Loss: 0.035 | Acc: 98.988% (38138/38528)
310 391 Loss: 0.035 | Acc: 98.993% (39407/39808)
320 391 Loss: 0.035 | Acc: 98.990% (40673/41088)
330 391 Loss: 0.035 | Acc: 98.995% (41942/42368)
340 391 Loss: 0.035 | Acc: 99.006% (43214/43648)
350 391 Loss: 0.034 | Acc: 99.007% (44482/44928)
360 391 Loss: 0.035 | Acc: 99.002% (45747/46208)
370 391 Loss: 0.035 | Acc: 98.993% (47010/47488)
380 391 Loss: 0.035 

210 391 Loss: 0.034 | Acc: 99.085% (26761/27008)
220 391 Loss: 0.034 | Acc: 99.070% (28025/28288)
230 391 Loss: 0.034 | Acc: 99.056% (29289/29568)
240 391 Loss: 0.034 | Acc: 99.063% (30559/30848)
250 391 Loss: 0.034 | Acc: 99.063% (31827/32128)
260 391 Loss: 0.034 | Acc: 99.063% (33095/33408)
270 391 Loss: 0.035 | Acc: 99.063% (34363/34688)
280 391 Loss: 0.034 | Acc: 99.066% (35632/35968)
290 391 Loss: 0.034 | Acc: 99.066% (36900/37248)
300 391 Loss: 0.034 | Acc: 99.050% (38162/38528)
310 391 Loss: 0.034 | Acc: 99.048% (39429/39808)
320 391 Loss: 0.035 | Acc: 99.041% (40694/41088)
330 391 Loss: 0.034 | Acc: 99.051% (41966/42368)
340 391 Loss: 0.034 | Acc: 99.045% (43231/43648)
350 391 Loss: 0.034 | Acc: 99.050% (44501/44928)
360 391 Loss: 0.034 | Acc: 99.035% (45762/46208)
370 391 Loss: 0.034 | Acc: 99.033% (47029/47488)
380 391 Loss: 0.034 | Acc: 99.024% (48292/48768)
390 391 Loss: 0.034 | Acc: 99.024% (49512/50000)
0 100 Loss: 0.222 | Acc: 93.000% (93/100)
50 100 Loss: 0.354 | Acc: 9

In [38]:
# ResNet32의 best_accuracy
best_accuracy

91.55

In [39]:
best_accuracy = 0
start_epoch = 0
net = resnet44()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 3.728 | Acc: 14.062% (18/128)
10 391 Loss: 2.812 | Acc: 11.435% (161/1408)
20 391 Loss: 2.642 | Acc: 13.356% (359/2688)
30 391 Loss: 2.542 | Acc: 14.390% (571/3968)
40 391 Loss: 2.466 | Acc: 15.053% (790/5248)
50 391 Loss: 2.388 | Acc: 16.789% (1096/6528)
60 391 Loss: 2.317 | Acc: 18.238% (1424/7808)
70 391 Loss: 2.267 | Acc: 19.355% (1759/9088)
80 391 Loss: 2.233 | Acc: 20.062% (2080/10368)
90 391 Loss: 2.208 | Acc: 20.639% (2404/11648)
100 391 Loss: 2.175 | Acc: 21.380% (2764/12928)
110 391 Loss: 2.145 | Acc: 22.234% (3159/14208)
120 391 Loss: 2.118 | Acc: 22.973% (3558/15488)
130 391 Loss: 2.094 | Acc: 23.575% (3953/16768)
140 391 Loss: 2.071 | Acc: 24.307% (4387/18048)
150 391 Loss: 2.052 | Acc: 24.959% (4824/19328)
160 391 Loss: 2.033 | Acc: 25.539% (5263/20608)
170 391 Loss: 2.019 | Acc: 26.037% (5699/21888)
180 391 Loss: 2.003 | Acc: 26.575% (6157/23168)
190 391 Loss: 1.988 | Acc: 27.025% (6607/24448)
200 391 Loss: 1.973 | Acc: 27.616% (7105/25728)
210 391 Loss: 1.95

20 391 Loss: 1.087 | Acc: 60.938% (1638/2688)
30 391 Loss: 1.083 | Acc: 60.862% (2415/3968)
40 391 Loss: 1.085 | Acc: 60.995% (3201/5248)
50 391 Loss: 1.087 | Acc: 60.692% (3962/6528)
60 391 Loss: 1.085 | Acc: 60.630% (4734/7808)
70 391 Loss: 1.084 | Acc: 60.585% (5506/9088)
80 391 Loss: 1.082 | Acc: 60.841% (6308/10368)
90 391 Loss: 1.081 | Acc: 61.092% (7116/11648)
100 391 Loss: 1.080 | Acc: 61.208% (7913/12928)
110 391 Loss: 1.079 | Acc: 61.233% (8700/14208)
120 391 Loss: 1.073 | Acc: 61.454% (9518/15488)
130 391 Loss: 1.075 | Acc: 61.403% (10296/16768)
140 391 Loss: 1.075 | Acc: 61.292% (11062/18048)
150 391 Loss: 1.076 | Acc: 61.232% (11835/19328)
160 391 Loss: 1.076 | Acc: 61.321% (12637/20608)
170 391 Loss: 1.076 | Acc: 61.408% (13441/21888)
180 391 Loss: 1.076 | Acc: 61.425% (14231/23168)
190 391 Loss: 1.077 | Acc: 61.392% (15009/24448)
200 391 Loss: 1.073 | Acc: 61.509% (15825/25728)
210 391 Loss: 1.073 | Acc: 61.493% (16608/27008)
220 391 Loss: 1.074 | Acc: 61.471% (17389/282

40 391 Loss: 0.857 | Acc: 69.531% (3649/5248)
50 391 Loss: 0.859 | Acc: 69.623% (4545/6528)
60 391 Loss: 0.858 | Acc: 69.749% (5446/7808)
70 391 Loss: 0.856 | Acc: 69.817% (6345/9088)
80 391 Loss: 0.854 | Acc: 69.907% (7248/10368)
90 391 Loss: 0.855 | Acc: 69.909% (8143/11648)
100 391 Loss: 0.850 | Acc: 69.926% (9040/12928)
110 391 Loss: 0.851 | Acc: 69.904% (9932/14208)
120 391 Loss: 0.851 | Acc: 69.983% (10839/15488)
130 391 Loss: 0.852 | Acc: 69.949% (11729/16768)
140 391 Loss: 0.850 | Acc: 70.041% (12641/18048)
150 391 Loss: 0.854 | Acc: 69.899% (13510/19328)
160 391 Loss: 0.852 | Acc: 70.021% (14430/20608)
170 391 Loss: 0.853 | Acc: 70.016% (15325/21888)
180 391 Loss: 0.851 | Acc: 70.088% (16238/23168)
190 391 Loss: 0.854 | Acc: 69.953% (17102/24448)
200 391 Loss: 0.853 | Acc: 69.920% (17989/25728)
210 391 Loss: 0.852 | Acc: 69.961% (18895/27008)
220 391 Loss: 0.852 | Acc: 69.970% (19793/28288)
230 391 Loss: 0.853 | Acc: 69.995% (20696/29568)
240 391 Loss: 0.854 | Acc: 70.011% (21

50 391 Loss: 0.700 | Acc: 74.985% (4895/6528)
60 391 Loss: 0.701 | Acc: 74.769% (5838/7808)
70 391 Loss: 0.701 | Acc: 75.033% (6819/9088)
80 391 Loss: 0.698 | Acc: 75.125% (7789/10368)
90 391 Loss: 0.700 | Acc: 75.146% (8753/11648)
100 391 Loss: 0.701 | Acc: 75.062% (9704/12928)
110 391 Loss: 0.703 | Acc: 75.113% (10672/14208)
120 391 Loss: 0.706 | Acc: 75.039% (11622/15488)
130 391 Loss: 0.703 | Acc: 75.149% (12601/16768)
140 391 Loss: 0.701 | Acc: 75.260% (13583/18048)
150 391 Loss: 0.702 | Acc: 75.290% (14552/19328)
160 391 Loss: 0.705 | Acc: 75.116% (15480/20608)
170 391 Loss: 0.709 | Acc: 74.968% (16409/21888)
180 391 Loss: 0.707 | Acc: 75.043% (17386/23168)
190 391 Loss: 0.706 | Acc: 75.086% (18357/24448)
200 391 Loss: 0.704 | Acc: 75.214% (19351/25728)
210 391 Loss: 0.704 | Acc: 75.167% (20301/27008)
220 391 Loss: 0.707 | Acc: 75.060% (21233/28288)
230 391 Loss: 0.708 | Acc: 75.091% (22203/29568)
240 391 Loss: 0.707 | Acc: 75.081% (23161/30848)
250 391 Loss: 0.708 | Acc: 75.078%

60 391 Loss: 0.601 | Acc: 79.060% (6173/7808)
70 391 Loss: 0.602 | Acc: 79.049% (7184/9088)
80 391 Loss: 0.602 | Acc: 78.974% (8188/10368)
90 391 Loss: 0.606 | Acc: 78.923% (9193/11648)
100 391 Loss: 0.603 | Acc: 79.030% (10217/12928)
110 391 Loss: 0.606 | Acc: 78.913% (11212/14208)
120 391 Loss: 0.608 | Acc: 78.868% (12215/15488)
130 391 Loss: 0.611 | Acc: 78.727% (13201/16768)
140 391 Loss: 0.614 | Acc: 78.734% (14210/18048)
150 391 Loss: 0.611 | Acc: 78.839% (15238/19328)
160 391 Loss: 0.612 | Acc: 78.736% (16226/20608)
170 391 Loss: 0.611 | Acc: 78.746% (17236/21888)
180 391 Loss: 0.609 | Acc: 78.785% (18253/23168)
190 391 Loss: 0.610 | Acc: 78.820% (19270/24448)
200 391 Loss: 0.610 | Acc: 78.774% (20267/25728)
210 391 Loss: 0.608 | Acc: 78.854% (21297/27008)
220 391 Loss: 0.609 | Acc: 78.828% (22299/28288)
230 391 Loss: 0.609 | Acc: 78.869% (23320/29568)
240 391 Loss: 0.609 | Acc: 78.812% (24312/30848)
250 391 Loss: 0.609 | Acc: 78.822% (25324/32128)
260 391 Loss: 0.609 | Acc: 78.

...

80 391 Loss: 0.022 | Acc: 99.354% (10301/10368)
90 391 Loss: 0.022 | Acc: 99.348% (11572/11648)
100 391 Loss: 0.023 | Acc: 99.319% (12840/12928)
110 391 Loss: 0.022 | Acc: 99.345% (14115/14208)
120 391 Loss: 0.023 | Acc: 99.335% (15385/15488)
130 391 Loss: 0.023 | Acc: 99.338% (16657/16768)
140 391 Loss: 0.023 | Acc: 99.352% (17931/18048)
150 391 Loss: 0.023 | Acc: 99.343% (19201/19328)
160 391 Loss: 0.023 | Acc: 99.350% (20474/20608)
170 391 Loss: 0.022 | Acc: 99.370% (21750/21888)
180 391 Loss: 0.023 | Acc: 99.340% (23015/23168)
190 391 Loss: 0.023 | Acc: 99.329% (24284/24448)
200 391 Loss: 0.023 | Acc: 99.335% (25557/25728)
210 391 Loss: 0.024 | Acc: 99.300% (26819/27008)
220 391 Loss: 0.024 | Acc: 99.289% (28087/28288)
230 391 Loss: 0.024 | Acc: 99.300% (29361/29568)
240 391 Loss: 0.023 | Acc: 99.316% (30637/30848)
250 391 Loss: 0.023 | Acc: 99.309% (31906/32128)
260 391 Loss: 0.023 | Acc: 99.312% (33178/33408)
270 391 Loss: 0.023 | Acc: 99.305% (34447/34688)
280 391 Loss: 0.023 | 

90 391 Loss: 0.020 | Acc: 99.425% (11581/11648)
100 391 Loss: 0.021 | Acc: 99.381% (12848/12928)
110 391 Loss: 0.021 | Acc: 99.374% (14119/14208)
120 391 Loss: 0.021 | Acc: 99.367% (15390/15488)
130 391 Loss: 0.022 | Acc: 99.350% (16659/16768)
140 391 Loss: 0.022 | Acc: 99.368% (17934/18048)
150 391 Loss: 0.022 | Acc: 99.369% (19206/19328)
160 391 Loss: 0.021 | Acc: 99.389% (20482/20608)
170 391 Loss: 0.021 | Acc: 99.388% (21754/21888)
180 391 Loss: 0.021 | Acc: 99.383% (23025/23168)
190 391 Loss: 0.021 | Acc: 99.374% (24295/24448)
200 391 Loss: 0.021 | Acc: 99.398% (25573/25728)
210 391 Loss: 0.021 | Acc: 99.393% (26844/27008)
220 391 Loss: 0.021 | Acc: 99.385% (28114/28288)
230 391 Loss: 0.021 | Acc: 99.384% (29386/29568)
240 391 Loss: 0.021 | Acc: 99.400% (30663/30848)
250 391 Loss: 0.021 | Acc: 99.412% (31939/32128)
260 391 Loss: 0.020 | Acc: 99.413% (33212/33408)
270 391 Loss: 0.020 | Acc: 99.412% (34484/34688)
280 391 Loss: 0.021 | Acc: 99.391% (35749/35968)
290 391 Loss: 0.021 |

100 391 Loss: 0.022 | Acc: 99.350% (12844/12928)
110 391 Loss: 0.021 | Acc: 99.367% (14118/14208)
120 391 Loss: 0.021 | Acc: 99.374% (15391/15488)
130 391 Loss: 0.021 | Acc: 99.386% (16665/16768)
140 391 Loss: 0.021 | Acc: 99.396% (17939/18048)
150 391 Loss: 0.021 | Acc: 99.379% (19208/19328)
160 391 Loss: 0.021 | Acc: 99.389% (20482/20608)
170 391 Loss: 0.021 | Acc: 99.365% (21749/21888)
180 391 Loss: 0.020 | Acc: 99.374% (23023/23168)
190 391 Loss: 0.020 | Acc: 99.391% (24299/24448)
200 391 Loss: 0.020 | Acc: 99.386% (25570/25728)
210 391 Loss: 0.020 | Acc: 99.389% (26843/27008)
220 391 Loss: 0.020 | Acc: 99.403% (28119/28288)
230 391 Loss: 0.020 | Acc: 99.405% (29392/29568)
240 391 Loss: 0.021 | Acc: 99.404% (30664/30848)
250 391 Loss: 0.021 | Acc: 99.399% (31935/32128)
260 391 Loss: 0.021 | Acc: 99.401% (33208/33408)
270 391 Loss: 0.021 | Acc: 99.406% (34482/34688)
280 391 Loss: 0.021 | Acc: 99.405% (35754/35968)
290 391 Loss: 0.021 | Acc: 99.412% (37029/37248)
300 391 Loss: 0.021 

110 391 Loss: 0.017 | Acc: 99.557% (14145/14208)
120 391 Loss: 0.017 | Acc: 99.561% (15420/15488)
130 391 Loss: 0.017 | Acc: 99.559% (16694/16768)
140 391 Loss: 0.017 | Acc: 99.535% (17964/18048)
150 391 Loss: 0.018 | Acc: 99.519% (19235/19328)
160 391 Loss: 0.018 | Acc: 99.524% (20510/20608)
170 391 Loss: 0.018 | Acc: 99.529% (21785/21888)
180 391 Loss: 0.018 | Acc: 99.525% (23058/23168)
190 391 Loss: 0.018 | Acc: 99.534% (24334/24448)
200 391 Loss: 0.018 | Acc: 99.526% (25606/25728)
210 391 Loss: 0.018 | Acc: 99.533% (26882/27008)
220 391 Loss: 0.018 | Acc: 99.526% (28154/28288)
230 391 Loss: 0.019 | Acc: 99.523% (29427/29568)
240 391 Loss: 0.019 | Acc: 99.527% (30702/30848)
250 391 Loss: 0.018 | Acc: 99.542% (31981/32128)
260 391 Loss: 0.018 | Acc: 99.539% (33254/33408)
270 391 Loss: 0.018 | Acc: 99.550% (34532/34688)
280 391 Loss: 0.018 | Acc: 99.541% (35803/35968)
290 391 Loss: 0.018 | Acc: 99.522% (37070/37248)
300 391 Loss: 0.018 | Acc: 99.517% (38342/38528)
310 391 Loss: 0.018 

120 391 Loss: 0.019 | Acc: 99.522% (15414/15488)
130 391 Loss: 0.019 | Acc: 99.487% (16682/16768)
140 391 Loss: 0.019 | Acc: 99.479% (17954/18048)
150 391 Loss: 0.019 | Acc: 99.488% (19229/19328)
160 391 Loss: 0.019 | Acc: 99.490% (20503/20608)
170 391 Loss: 0.019 | Acc: 99.479% (21774/21888)
180 391 Loss: 0.019 | Acc: 99.491% (23050/23168)
190 391 Loss: 0.019 | Acc: 99.489% (24323/24448)
200 391 Loss: 0.019 | Acc: 99.487% (25596/25728)
210 391 Loss: 0.019 | Acc: 99.485% (26869/27008)
220 391 Loss: 0.019 | Acc: 99.480% (28141/28288)
230 391 Loss: 0.019 | Acc: 99.486% (29416/29568)
240 391 Loss: 0.019 | Acc: 99.478% (30687/30848)
250 391 Loss: 0.019 | Acc: 99.474% (31959/32128)
260 391 Loss: 0.019 | Acc: 99.488% (33237/33408)
270 391 Loss: 0.019 | Acc: 99.487% (34510/34688)
280 391 Loss: 0.019 | Acc: 99.480% (35781/35968)
290 391 Loss: 0.019 | Acc: 99.482% (37055/37248)
300 391 Loss: 0.018 | Acc: 99.481% (38328/38528)
310 391 Loss: 0.019 | Acc: 99.470% (39597/39808)
320 391 Loss: 0.019 

In [40]:
# ResNet44의 best_accuracy
best_accuracy

92.19

## lr = 0.005 and Dropout rate 0.3 -> 0.5

In [41]:
class ResNet(nn.Module):
  def __init__(self, block, num_blocks, num_classes=10):
    super(ResNet, self).__init__()
    
    self.in_planes = 16

    self.dropout = nn.Dropout(0.5)

    self.conv1 = nn.Conv2d(3, 16, kernel_size=3, stride=1, padding=1, bias=False)
    self.bn1 = nn.BatchNorm2d(16)


    # feature map : 32 x 32 x 16
    self.layer1 = self._make_layer(block, 16, num_blocks[0], stride=1)
    # feature map : 16 x 16 x 32
    self.layer2 = self._make_layer(block, 32, num_blocks[1], stride=2)
    # feature map : 8 x 8 x 64
    self.layer3 = self._make_layer(block, 64, num_blocks[2], stride=2)
    # 마지막 클래스 예측 (Linear)
    self.fc_out = nn.Linear(64, num_classes)

    self.apply(_weights_init)

  
  def _make_layer(self, block, planes, num_blocks, stride):
    # 처음 stride만 2, 이후 1
    strides = [stride] + [1]*(num_blocks-1)
    layers = []
    for stride in strides:
        layers.append(block(self.in_planes, planes, stride))
        self.in_planes = planes * block.expansion
    return nn.Sequential(*layers)

  def forward(self, x):
    out = F.relu(self.bn1(self.conv1(x)))
    #out = self.dropout(out)
    out = self.layer1(out)
    out = self.dropout(out)
    out = self.layer2(out)
    out = self.dropout(out)
    out = self.layer3(out)
    out = F.avg_pool2d(out, out.size()[3])
    out = out.view(out.size(0),-1)
    out = self.fc_out(out)
    return out

In [43]:
best_accuracy = 0
start_epoch = 0

net = resnet20()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True
    
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.005, momentum=0.8, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 4.408 | Acc: 7.812% (10/128)
10 391 Loss: 3.013 | Acc: 10.227% (144/1408)
20 391 Loss: 2.711 | Acc: 11.458% (308/2688)
30 391 Loss: 2.557 | Acc: 13.130% (521/3968)
40 391 Loss: 2.471 | Acc: 14.024% (736/5248)
50 391 Loss: 2.414 | Acc: 14.691% (959/6528)
60 391 Loss: 2.366 | Acc: 15.804% (1234/7808)
70 391 Loss: 2.328 | Acc: 16.802% (1527/9088)
80 391 Loss: 2.300 | Acc: 17.467% (1811/10368)
90 391 Loss: 2.274 | Acc: 18.046% (2102/11648)
100 391 Loss: 2.250 | Acc: 18.711% (2419/12928)
110 391 Loss: 2.227 | Acc: 19.376% (2753/14208)
120 391 Loss: 2.209 | Acc: 19.635% (3041/15488)
130 391 Loss: 2.194 | Acc: 19.913% (3339/16768)
140 391 Loss: 2.178 | Acc: 20.229% (3651/18048)
150 391 Loss: 2.167 | Acc: 20.463% (3955/19328)
160 391 Loss: 2.156 | Acc: 20.725% (4271/20608)
170 391 Loss: 2.144 | Acc: 20.952% (4586/21888)
180 391 Loss: 2.132 | Acc: 21.206% (4913/23168)
190 391 Loss: 2.123 | Acc: 21.417% (5236/24448)
200 391 Loss: 2.115 | Acc: 21.688% (5580/25728)
210 391 Loss: 2.105 

30 391 Loss: 1.571 | Acc: 42.490% (1686/3968)
40 391 Loss: 1.565 | Acc: 42.511% (2231/5248)
50 391 Loss: 1.574 | Acc: 42.126% (2750/6528)
60 391 Loss: 1.565 | Acc: 42.354% (3307/7808)
70 391 Loss: 1.565 | Acc: 42.221% (3837/9088)
80 391 Loss: 1.566 | Acc: 42.014% (4356/10368)
90 391 Loss: 1.562 | Acc: 42.256% (4922/11648)
100 391 Loss: 1.561 | Acc: 42.234% (5460/12928)
110 391 Loss: 1.561 | Acc: 42.131% (5986/14208)
120 391 Loss: 1.555 | Acc: 42.200% (6536/15488)
130 391 Loss: 1.552 | Acc: 42.116% (7062/16768)
140 391 Loss: 1.554 | Acc: 41.977% (7576/18048)
150 391 Loss: 1.556 | Acc: 41.763% (8072/19328)
160 391 Loss: 1.557 | Acc: 41.727% (8599/20608)
170 391 Loss: 1.556 | Acc: 41.758% (9140/21888)
180 391 Loss: 1.555 | Acc: 41.829% (9691/23168)
190 391 Loss: 1.554 | Acc: 41.815% (10223/24448)
200 391 Loss: 1.554 | Acc: 41.818% (10759/25728)
210 391 Loss: 1.553 | Acc: 41.884% (11312/27008)
220 391 Loss: 1.552 | Acc: 41.880% (11847/28288)
230 391 Loss: 1.552 | Acc: 41.883% (12384/29568)

50 391 Loss: 1.338 | Acc: 51.854% (3385/6528)
60 391 Loss: 1.338 | Acc: 51.639% (4032/7808)
70 391 Loss: 1.341 | Acc: 51.166% (4650/9088)
80 391 Loss: 1.345 | Acc: 50.936% (5281/10368)
90 391 Loss: 1.347 | Acc: 50.841% (5922/11648)
100 391 Loss: 1.348 | Acc: 50.951% (6587/12928)
110 391 Loss: 1.344 | Acc: 50.978% (7243/14208)
120 391 Loss: 1.348 | Acc: 50.775% (7864/15488)
130 391 Loss: 1.349 | Acc: 50.728% (8506/16768)
140 391 Loss: 1.347 | Acc: 50.920% (9190/18048)
150 391 Loss: 1.348 | Acc: 50.900% (9838/19328)
160 391 Loss: 1.345 | Acc: 51.024% (10515/20608)
170 391 Loss: 1.345 | Acc: 50.932% (11148/21888)
180 391 Loss: 1.344 | Acc: 50.980% (11811/23168)
190 391 Loss: 1.340 | Acc: 51.108% (12495/24448)
200 391 Loss: 1.340 | Acc: 51.065% (13138/25728)
210 391 Loss: 1.338 | Acc: 51.055% (13789/27008)
220 391 Loss: 1.337 | Acc: 51.114% (14459/28288)
230 391 Loss: 1.341 | Acc: 51.055% (15096/29568)
240 391 Loss: 1.339 | Acc: 51.028% (15741/30848)
250 391 Loss: 1.340 | Acc: 50.987% (163

70 391 Loss: 1.164 | Acc: 58.231% (5292/9088)
80 391 Loss: 1.159 | Acc: 58.382% (6053/10368)
90 391 Loss: 1.156 | Acc: 58.456% (6809/11648)
100 391 Loss: 1.158 | Acc: 58.261% (7532/12928)
110 391 Loss: 1.158 | Acc: 58.242% (8275/14208)
120 391 Loss: 1.156 | Acc: 58.400% (9045/15488)
130 391 Loss: 1.157 | Acc: 58.379% (9789/16768)
140 391 Loss: 1.157 | Acc: 58.389% (10538/18048)
150 391 Loss: 1.160 | Acc: 58.325% (11273/19328)
160 391 Loss: 1.160 | Acc: 58.230% (12000/20608)
170 391 Loss: 1.161 | Acc: 58.251% (12750/21888)
180 391 Loss: 1.159 | Acc: 58.352% (13519/23168)
190 391 Loss: 1.158 | Acc: 58.414% (14281/24448)
200 391 Loss: 1.157 | Acc: 58.431% (15033/25728)
210 391 Loss: 1.154 | Acc: 58.553% (15814/27008)
220 391 Loss: 1.151 | Acc: 58.693% (16603/28288)
230 391 Loss: 1.152 | Acc: 58.658% (17344/29568)
240 391 Loss: 1.151 | Acc: 58.659% (18095/30848)
250 391 Loss: 1.153 | Acc: 58.603% (18828/32128)
260 391 Loss: 1.153 | Acc: 58.615% (19582/33408)
270 391 Loss: 1.150 | Acc: 58.6

90 391 Loss: 1.057 | Acc: 62.285% (7255/11648)
100 391 Loss: 1.058 | Acc: 62.067% (8024/12928)
110 391 Loss: 1.060 | Acc: 61.937% (8800/14208)
120 391 Loss: 1.061 | Acc: 61.861% (9581/15488)
130 391 Loss: 1.061 | Acc: 61.868% (10374/16768)
140 391 Loss: 1.062 | Acc: 61.807% (11155/18048)
150 391 Loss: 1.061 | Acc: 61.977% (11979/19328)
160 391 Loss: 1.061 | Acc: 62.015% (12780/20608)
170 391 Loss: 1.062 | Acc: 61.929% (13555/21888)
180 391 Loss: 1.059 | Acc: 62.004% (14365/23168)
190 391 Loss: 1.058 | Acc: 62.034% (15166/24448)
200 391 Loss: 1.057 | Acc: 62.061% (15967/25728)
210 391 Loss: 1.057 | Acc: 62.030% (16753/27008)
220 391 Loss: 1.056 | Acc: 61.998% (17538/28288)
230 391 Loss: 1.056 | Acc: 61.979% (18326/29568)
240 391 Loss: 1.056 | Acc: 61.975% (19118/30848)
250 391 Loss: 1.054 | Acc: 62.036% (19931/32128)
260 391 Loss: 1.055 | Acc: 61.997% (20712/33408)
270 391 Loss: 1.053 | Acc: 62.065% (21529/34688)
280 391 Loss: 1.052 | Acc: 62.116% (22342/35968)
290 391 Loss: 1.052 | Acc

...

200 391 Loss: 0.395 | Acc: 86.198% (22177/25728)
210 391 Loss: 0.396 | Acc: 86.193% (23279/27008)
220 391 Loss: 0.396 | Acc: 86.171% (24376/28288)
230 391 Loss: 0.398 | Acc: 86.093% (25456/29568)
240 391 Loss: 0.399 | Acc: 86.041% (26542/30848)
250 391 Loss: 0.399 | Acc: 86.025% (27638/32128)
260 391 Loss: 0.401 | Acc: 85.935% (28709/33408)
270 391 Loss: 0.400 | Acc: 85.929% (29807/34688)
280 391 Loss: 0.401 | Acc: 85.871% (30886/35968)
290 391 Loss: 0.402 | Acc: 85.827% (31969/37248)
300 391 Loss: 0.401 | Acc: 85.834% (33070/38528)
310 391 Loss: 0.401 | Acc: 85.822% (34164/39808)
320 391 Loss: 0.401 | Acc: 85.833% (35267/41088)
330 391 Loss: 0.400 | Acc: 85.883% (36387/42368)
340 391 Loss: 0.399 | Acc: 85.921% (37503/43648)
350 391 Loss: 0.400 | Acc: 85.920% (38602/44928)
360 391 Loss: 0.400 | Acc: 85.933% (39708/46208)
370 391 Loss: 0.399 | Acc: 85.950% (40816/47488)
380 391 Loss: 0.399 | Acc: 85.946% (41914/48768)
390 391 Loss: 0.400 | Acc: 85.924% (42962/50000)
0 100 Loss: 0.419 | 

210 391 Loss: 0.398 | Acc: 86.049% (23240/27008)
220 391 Loss: 0.398 | Acc: 86.044% (24340/28288)
230 391 Loss: 0.398 | Acc: 86.039% (25440/29568)
240 391 Loss: 0.398 | Acc: 86.048% (26544/30848)
250 391 Loss: 0.399 | Acc: 86.028% (27639/32128)
260 391 Loss: 0.398 | Acc: 86.039% (28744/33408)
270 391 Loss: 0.399 | Acc: 86.010% (29835/34688)
280 391 Loss: 0.400 | Acc: 85.968% (30921/35968)
290 391 Loss: 0.400 | Acc: 85.983% (32027/37248)
300 391 Loss: 0.400 | Acc: 85.989% (33130/38528)
310 391 Loss: 0.399 | Acc: 86.008% (34238/39808)
320 391 Loss: 0.399 | Acc: 86.035% (35350/41088)
330 391 Loss: 0.398 | Acc: 86.086% (36473/42368)
340 391 Loss: 0.398 | Acc: 86.066% (37566/43648)
350 391 Loss: 0.398 | Acc: 86.082% (38675/44928)
360 391 Loss: 0.398 | Acc: 86.089% (39780/46208)
370 391 Loss: 0.398 | Acc: 86.119% (40896/47488)
380 391 Loss: 0.398 | Acc: 86.128% (42003/48768)
390 391 Loss: 0.398 | Acc: 86.128% (43064/50000)
0 100 Loss: 0.425 | Acc: 82.000% (82/100)
50 100 Loss: 0.487 | Acc: 8

220 391 Loss: 0.393 | Acc: 86.266% (24403/28288)
230 391 Loss: 0.393 | Acc: 86.303% (25518/29568)
240 391 Loss: 0.395 | Acc: 86.239% (26603/30848)
250 391 Loss: 0.396 | Acc: 86.233% (27705/32128)
260 391 Loss: 0.396 | Acc: 86.228% (28807/33408)
270 391 Loss: 0.397 | Acc: 86.174% (29892/34688)
280 391 Loss: 0.395 | Acc: 86.257% (31025/35968)
290 391 Loss: 0.395 | Acc: 86.268% (32133/37248)
300 391 Loss: 0.394 | Acc: 86.303% (33251/38528)
310 391 Loss: 0.395 | Acc: 86.292% (34351/39808)
320 391 Loss: 0.394 | Acc: 86.320% (35467/41088)
330 391 Loss: 0.394 | Acc: 86.303% (36565/42368)
340 391 Loss: 0.395 | Acc: 86.279% (37659/43648)
350 391 Loss: 0.396 | Acc: 86.242% (38747/44928)
360 391 Loss: 0.396 | Acc: 86.247% (39853/46208)
370 391 Loss: 0.396 | Acc: 86.237% (40952/47488)
380 391 Loss: 0.397 | Acc: 86.190% (42033/48768)
390 391 Loss: 0.397 | Acc: 86.210% (43105/50000)
0 100 Loss: 0.408 | Acc: 85.000% (85/100)
50 100 Loss: 0.492 | Acc: 83.902% (4279/5100)
epoch :  189 84.51
0 391 Loss:

230 391 Loss: 0.389 | Acc: 86.563% (25595/29568)
240 391 Loss: 0.388 | Acc: 86.579% (26708/30848)
250 391 Loss: 0.389 | Acc: 86.554% (27808/32128)
260 391 Loss: 0.389 | Acc: 86.545% (28913/33408)
270 391 Loss: 0.388 | Acc: 86.641% (30054/34688)
280 391 Loss: 0.389 | Acc: 86.591% (31145/35968)
290 391 Loss: 0.389 | Acc: 86.601% (32257/37248)
300 391 Loss: 0.389 | Acc: 86.568% (33353/38528)
310 391 Loss: 0.389 | Acc: 86.568% (34461/39808)
320 391 Loss: 0.388 | Acc: 86.561% (35566/41088)
330 391 Loss: 0.388 | Acc: 86.542% (36666/42368)
340 391 Loss: 0.389 | Acc: 86.503% (37757/43648)
350 391 Loss: 0.390 | Acc: 86.494% (38860/44928)
360 391 Loss: 0.390 | Acc: 86.511% (39975/46208)
370 391 Loss: 0.390 | Acc: 86.496% (41075/47488)
380 391 Loss: 0.390 | Acc: 86.518% (42193/48768)
390 391 Loss: 0.390 | Acc: 86.512% (43256/50000)
0 100 Loss: 0.410 | Acc: 84.000% (84/100)
50 100 Loss: 0.489 | Acc: 84.059% (4287/5100)
epoch :  193 84.51
0 391 Loss: 0.287 | Acc: 89.062% (114/128)
10 391 Loss: 0.36

240 391 Loss: 0.398 | Acc: 86.275% (26614/30848)
250 391 Loss: 0.398 | Acc: 86.274% (27718/32128)
260 391 Loss: 0.398 | Acc: 86.300% (28831/33408)
270 391 Loss: 0.397 | Acc: 86.278% (29928/34688)
280 391 Loss: 0.398 | Acc: 86.235% (31017/35968)
290 391 Loss: 0.398 | Acc: 86.244% (32124/37248)
300 391 Loss: 0.397 | Acc: 86.259% (33234/38528)
310 391 Loss: 0.398 | Acc: 86.231% (34327/39808)
320 391 Loss: 0.398 | Acc: 86.210% (35422/41088)
330 391 Loss: 0.398 | Acc: 86.218% (36529/42368)
340 391 Loss: 0.398 | Acc: 86.203% (37626/43648)
350 391 Loss: 0.399 | Acc: 86.169% (38714/44928)
360 391 Loss: 0.398 | Acc: 86.180% (39822/46208)
370 391 Loss: 0.397 | Acc: 86.207% (40938/47488)
380 391 Loss: 0.397 | Acc: 86.204% (42040/48768)
390 391 Loss: 0.397 | Acc: 86.206% (43103/50000)
0 100 Loss: 0.401 | Acc: 84.000% (84/100)
50 100 Loss: 0.491 | Acc: 83.941% (4281/5100)
epoch :  197 84.51
0 391 Loss: 0.504 | Acc: 82.031% (105/128)
10 391 Loss: 0.407 | Acc: 86.009% (1211/1408)
20 391 Loss: 0.410 |

In [44]:
best_accuracy

84.51

## lr = 0.01 & optimizer = Adam

In [ ]:
best_accuracy = 0
start_epoch = 0

net = resnet20()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True
    
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(net.parameters(), lr=0.01)

#decay_epoch = [32000, 48000]
#scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=decay_epoch, gamma=0.1)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 5.048 | Acc: 10.938% (14/128)
10 391 Loss: 2.857 | Acc: 14.986% (211/1408)
20 391 Loss: 2.495 | Acc: 17.522% (471/2688)
30 391 Loss: 2.346 | Acc: 19.657% (780/3968)
40 391 Loss: 2.261 | Acc: 20.541% (1078/5248)
50 391 Loss: 2.193 | Acc: 21.844% (1426/6528)
60 391 Loss: 2.137 | Acc: 23.156% (1808/7808)
70 391 Loss: 2.093 | Acc: 24.164% (2196/9088)
80 391 Loss: 2.057 | Acc: 25.029% (2595/10368)
90 391 Loss: 2.034 | Acc: 25.464% (2966/11648)
100 391 Loss: 2.007 | Acc: 26.300% (3400/12928)
110 391 Loss: 1.982 | Acc: 27.048% (3843/14208)
120 391 Loss: 1.959 | Acc: 27.641% (4281/15488)
130 391 Loss: 1.937 | Acc: 28.364% (4756/16768)
140 391 Loss: 1.919 | Acc: 28.945% (5224/18048)
150 391 Loss: 1.900 | Acc: 29.558% (5713/19328)
160 391 Loss: 1.882 | Acc: 30.202% (6224/20608)
170 391 Loss: 1.872 | Acc: 30.473% (6670/21888)
180 391 Loss: 1.860 | Acc: 30.801% (7136/23168)
190 391 Loss: 1.848 | Acc: 31.303% (7653/24448)
200 391 Loss: 1.837 | Acc: 31.697% (8155/25728)
210 391 Loss: 1.8

20 391 Loss: 0.927 | Acc: 66.964% (1800/2688)
30 391 Loss: 0.920 | Acc: 66.961% (2657/3968)
40 391 Loss: 0.907 | Acc: 67.473% (3541/5248)
50 391 Loss: 0.911 | Acc: 67.448% (4403/6528)
60 391 Loss: 0.909 | Acc: 67.853% (5298/7808)
70 391 Loss: 0.907 | Acc: 67.826% (6164/9088)
80 391 Loss: 0.906 | Acc: 67.728% (7022/10368)
90 391 Loss: 0.907 | Acc: 67.720% (7888/11648)
100 391 Loss: 0.908 | Acc: 67.706% (8753/12928)
110 391 Loss: 0.906 | Acc: 67.793% (9632/14208)
120 391 Loss: 0.909 | Acc: 67.639% (10476/15488)
130 391 Loss: 0.906 | Acc: 67.677% (11348/16768)
140 391 Loss: 0.902 | Acc: 67.825% (12241/18048)
150 391 Loss: 0.902 | Acc: 67.870% (13118/19328)
160 391 Loss: 0.903 | Acc: 67.901% (13993/20608)
170 391 Loss: 0.900 | Acc: 68.037% (14892/21888)
180 391 Loss: 0.898 | Acc: 68.128% (15784/23168)
190 391 Loss: 0.898 | Acc: 68.145% (16660/24448)
200 391 Loss: 0.898 | Acc: 68.078% (17515/25728)
210 391 Loss: 0.897 | Acc: 68.172% (18412/27008)
220 391 Loss: 0.898 | Acc: 68.146% (19277/28

30 391 Loss: 0.680 | Acc: 76.537% (3037/3968)
40 391 Loss: 0.680 | Acc: 76.296% (4004/5248)
50 391 Loss: 0.684 | Acc: 76.057% (4965/6528)
60 391 Loss: 0.688 | Acc: 75.961% (5931/7808)
70 391 Loss: 0.692 | Acc: 75.880% (6896/9088)
80 391 Loss: 0.690 | Acc: 75.839% (7863/10368)
90 391 Loss: 0.687 | Acc: 75.962% (8848/11648)
100 391 Loss: 0.693 | Acc: 75.688% (9785/12928)
110 391 Loss: 0.695 | Acc: 75.690% (10754/14208)
120 391 Loss: 0.692 | Acc: 75.807% (11741/15488)
130 391 Loss: 0.687 | Acc: 75.996% (12743/16768)
140 391 Loss: 0.685 | Acc: 76.025% (13721/18048)
150 391 Loss: 0.684 | Acc: 76.102% (14709/19328)
160 391 Loss: 0.686 | Acc: 76.072% (15677/20608)
170 391 Loss: 0.684 | Acc: 76.142% (16666/21888)
180 391 Loss: 0.684 | Acc: 76.230% (17661/23168)
190 391 Loss: 0.683 | Acc: 76.305% (18655/24448)
200 391 Loss: 0.683 | Acc: 76.240% (19615/25728)
210 391 Loss: 0.682 | Acc: 76.270% (20599/27008)
220 391 Loss: 0.684 | Acc: 76.230% (21564/28288)
230 391 Loss: 0.683 | Acc: 76.275% (2255

40 391 Loss: 0.574 | Acc: 80.469% (4223/5248)
50 391 Loss: 0.584 | Acc: 80.407% (5249/6528)
60 391 Loss: 0.586 | Acc: 80.149% (6258/7808)
70 391 Loss: 0.579 | Acc: 80.260% (7294/9088)
80 391 Loss: 0.583 | Acc: 80.141% (8309/10368)
90 391 Loss: 0.579 | Acc: 80.228% (9345/11648)
100 391 Loss: 0.577 | Acc: 80.275% (10378/12928)
110 391 Loss: 0.577 | Acc: 80.244% (11401/14208)
120 391 Loss: 0.576 | Acc: 80.152% (12414/15488)
130 391 Loss: 0.575 | Acc: 80.194% (13447/16768)
140 391 Loss: 0.573 | Acc: 80.197% (14474/18048)
150 391 Loss: 0.573 | Acc: 80.257% (15512/19328)
160 391 Loss: 0.576 | Acc: 80.153% (16518/20608)
170 391 Loss: 0.577 | Acc: 80.144% (17542/21888)
180 391 Loss: 0.575 | Acc: 80.154% (18570/23168)
190 391 Loss: 0.577 | Acc: 79.978% (19553/24448)
200 391 Loss: 0.576 | Acc: 80.072% (20601/25728)
210 391 Loss: 0.575 | Acc: 80.102% (21634/27008)
220 391 Loss: 0.574 | Acc: 80.204% (22688/28288)
230 391 Loss: 0.576 | Acc: 80.120% (23690/29568)
240 391 Loss: 0.575 | Acc: 80.148% (

50 391 Loss: 0.515 | Acc: 82.445% (5382/6528)
60 391 Loss: 0.528 | Acc: 81.801% (6387/7808)
70 391 Loss: 0.527 | Acc: 81.844% (7438/9088)
80 391 Loss: 0.525 | Acc: 81.896% (8491/10368)
90 391 Loss: 0.524 | Acc: 81.963% (9547/11648)
100 391 Loss: 0.524 | Acc: 82.093% (10613/12928)
110 391 Loss: 0.522 | Acc: 82.193% (11678/14208)
120 391 Loss: 0.521 | Acc: 82.186% (12729/15488)
130 391 Loss: 0.521 | Acc: 82.121% (13770/16768)
140 391 Loss: 0.521 | Acc: 82.042% (14807/18048)
150 391 Loss: 0.521 | Acc: 82.011% (15851/19328)
160 391 Loss: 0.520 | Acc: 82.046% (16908/20608)
170 391 Loss: 0.518 | Acc: 82.063% (17962/21888)
180 391 Loss: 0.516 | Acc: 82.105% (19022/23168)
190 391 Loss: 0.517 | Acc: 82.080% (20067/24448)
200 391 Loss: 0.517 | Acc: 82.074% (21116/25728)
210 391 Loss: 0.516 | Acc: 82.102% (22174/27008)
220 391 Loss: 0.514 | Acc: 82.134% (23234/28288)
230 391 Loss: 0.514 | Acc: 82.109% (24278/29568)
240 391 Loss: 0.513 | Acc: 82.161% (25345/30848)
250 391 Loss: 0.513 | Acc: 82.190

...

390 391 Loss: 0.114 | Acc: 95.892% (47946/50000)
0 100 Loss: 0.355 | Acc: 92.000% (92/100)
50 100 Loss: 0.450 | Acc: 89.137% (4546/5100)
epoch :  144 89.75
0 391 Loss: 0.064 | Acc: 97.656% (125/128)
10 391 Loss: 0.099 | Acc: 96.307% (1356/1408)
20 391 Loss: 0.107 | Acc: 95.908% (2578/2688)
30 391 Loss: 0.108 | Acc: 95.993% (3809/3968)
40 391 Loss: 0.106 | Acc: 96.094% (5043/5248)
50 391 Loss: 0.106 | Acc: 96.124% (6275/6528)
60 391 Loss: 0.106 | Acc: 96.094% (7503/7808)
70 391 Loss: 0.110 | Acc: 95.907% (8716/9088)
80 391 Loss: 0.110 | Acc: 95.930% (9946/10368)
90 391 Loss: 0.111 | Acc: 95.956% (11177/11648)
100 391 Loss: 0.110 | Acc: 95.993% (12410/12928)
110 391 Loss: 0.112 | Acc: 95.932% (13630/14208)
120 391 Loss: 0.110 | Acc: 96.023% (14872/15488)
130 391 Loss: 0.110 | Acc: 96.046% (16105/16768)
140 391 Loss: 0.110 | Acc: 96.000% (17326/18048)
150 391 Loss: 0.110 | Acc: 95.944% (18544/19328)
160 391 Loss: 0.110 | Acc: 95.963% (19776/20608)
170 391 Loss: 0.110 | Acc: 95.975% (21007

0 100 Loss: 0.336 | Acc: 92.000% (92/100)
50 100 Loss: 0.438 | Acc: 89.451% (4562/5100)
epoch :  148 90.01
0 391 Loss: 0.115 | Acc: 96.094% (123/128)
10 391 Loss: 0.103 | Acc: 96.094% (1353/1408)
20 391 Loss: 0.101 | Acc: 96.354% (2590/2688)
30 391 Loss: 0.101 | Acc: 96.321% (3822/3968)
40 391 Loss: 0.106 | Acc: 96.170% (5047/5248)
50 391 Loss: 0.104 | Acc: 96.232% (6282/6528)
60 391 Loss: 0.105 | Acc: 96.247% (7515/7808)
70 391 Loss: 0.110 | Acc: 96.061% (8730/9088)
80 391 Loss: 0.109 | Acc: 96.046% (9958/10368)
90 391 Loss: 0.110 | Acc: 95.999% (11182/11648)
100 391 Loss: 0.110 | Acc: 96.001% (12411/12928)
110 391 Loss: 0.111 | Acc: 96.009% (13641/14208)
120 391 Loss: 0.111 | Acc: 96.049% (14876/15488)
130 391 Loss: 0.110 | Acc: 96.130% (16119/16768)
140 391 Loss: 0.110 | Acc: 96.116% (17347/18048)
150 391 Loss: 0.110 | Acc: 96.068% (18568/19328)
160 391 Loss: 0.110 | Acc: 96.079% (19800/20608)
170 391 Loss: 0.109 | Acc: 96.075% (21029/21888)
180 391 Loss: 0.109 | Acc: 96.085% (22261

epoch :  152 90.01
0 391 Loss: 0.206 | Acc: 93.750% (120/128)
10 391 Loss: 0.110 | Acc: 96.449% (1358/1408)
20 391 Loss: 0.110 | Acc: 96.429% (2592/2688)
30 391 Loss: 0.109 | Acc: 96.346% (3823/3968)
40 391 Loss: 0.107 | Acc: 96.341% (5056/5248)
50 391 Loss: 0.106 | Acc: 96.369% (6291/6528)
60 391 Loss: 0.104 | Acc: 96.440% (7530/7808)
70 391 Loss: 0.102 | Acc: 96.479% (8768/9088)
80 391 Loss: 0.102 | Acc: 96.480% (10003/10368)
90 391 Loss: 0.102 | Acc: 96.454% (11235/11648)
100 391 Loss: 0.104 | Acc: 96.279% (12447/12928)
110 391 Loss: 0.104 | Acc: 96.340% (13688/14208)
120 391 Loss: 0.105 | Acc: 96.281% (14912/15488)
130 391 Loss: 0.104 | Acc: 96.255% (16140/16768)
140 391 Loss: 0.104 | Acc: 96.254% (17372/18048)
150 391 Loss: 0.107 | Acc: 96.177% (18589/19328)
160 391 Loss: 0.107 | Acc: 96.162% (19817/20608)
170 391 Loss: 0.106 | Acc: 96.181% (21052/21888)
180 391 Loss: 0.106 | Acc: 96.219% (22292/23168)
190 391 Loss: 0.105 | Acc: 96.253% (23532/24448)
200 391 Loss: 0.105 | Acc: 96.

10 391 Loss: 0.093 | Acc: 96.733% (1362/1408)
20 391 Loss: 0.101 | Acc: 96.205% (2586/2688)
30 391 Loss: 0.095 | Acc: 96.321% (3822/3968)
40 391 Loss: 0.098 | Acc: 96.265% (5052/5248)
50 391 Loss: 0.096 | Acc: 96.400% (6293/6528)
60 391 Loss: 0.098 | Acc: 96.299% (7519/7808)
70 391 Loss: 0.097 | Acc: 96.314% (8753/9088)
80 391 Loss: 0.097 | Acc: 96.277% (9982/10368)
90 391 Loss: 0.096 | Acc: 96.386% (11227/11648)
100 391 Loss: 0.097 | Acc: 96.388% (12461/12928)
110 391 Loss: 0.098 | Acc: 96.396% (13696/14208)
120 391 Loss: 0.098 | Acc: 96.346% (14922/15488)
130 391 Loss: 0.098 | Acc: 96.392% (16163/16768)
140 391 Loss: 0.097 | Acc: 96.459% (17409/18048)
150 391 Loss: 0.097 | Acc: 96.466% (18645/19328)
160 391 Loss: 0.097 | Acc: 96.472% (19881/20608)
170 391 Loss: 0.096 | Acc: 96.478% (21117/21888)
180 391 Loss: 0.096 | Acc: 96.508% (22359/23168)
190 391 Loss: 0.096 | Acc: 96.499% (23592/24448)
200 391 Loss: 0.097 | Acc: 96.486% (24824/25728)
210 391 Loss: 0.097 | Acc: 96.479% (26057/27

20 391 Loss: 0.096 | Acc: 96.466% (2593/2688)
30 391 Loss: 0.092 | Acc: 96.699% (3837/3968)
40 391 Loss: 0.093 | Acc: 96.627% (5071/5248)
50 391 Loss: 0.098 | Acc: 96.461% (6297/6528)
60 391 Loss: 0.095 | Acc: 96.555% (7539/7808)
70 391 Loss: 0.095 | Acc: 96.523% (8772/9088)
80 391 Loss: 0.098 | Acc: 96.499% (10005/10368)
90 391 Loss: 0.097 | Acc: 96.497% (11240/11648)
100 391 Loss: 0.096 | Acc: 96.527% (12479/12928)
110 391 Loss: 0.095 | Acc: 96.608% (13726/14208)
120 391 Loss: 0.096 | Acc: 96.559% (14955/15488)
130 391 Loss: 0.096 | Acc: 96.589% (16196/16768)
140 391 Loss: 0.096 | Acc: 96.581% (17431/18048)
150 391 Loss: 0.096 | Acc: 96.565% (18664/19328)
160 391 Loss: 0.096 | Acc: 96.526% (19892/20608)
170 391 Loss: 0.096 | Acc: 96.532% (21129/21888)
180 391 Loss: 0.096 | Acc: 96.538% (22366/23168)
190 391 Loss: 0.096 | Acc: 96.527% (23599/24448)
200 391 Loss: 0.096 | Acc: 96.549% (24840/25728)
210 391 Loss: 0.096 | Acc: 96.508% (26065/27008)
220 391 Loss: 0.096 | Acc: 96.472% (2729

In [47]:
for epoch in range(start_epoch, start_epoch+100):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 0.600 | Acc: 78.125% (100/128)
10 391 Loss: 0.468 | Acc: 84.020% (1183/1408)
20 391 Loss: 0.522 | Acc: 82.329% (2213/2688)
30 391 Loss: 0.514 | Acc: 82.334% (3267/3968)
40 391 Loss: 0.499 | Acc: 82.565% (4333/5248)
50 391 Loss: 0.496 | Acc: 82.368% (5377/6528)
60 391 Loss: 0.492 | Acc: 82.480% (6440/7808)
70 391 Loss: 0.490 | Acc: 82.504% (7498/9088)
80 391 Loss: 0.488 | Acc: 82.793% (8584/10368)
90 391 Loss: 0.487 | Acc: 82.778% (9642/11648)
100 391 Loss: 0.485 | Acc: 83.014% (10732/12928)
110 391 Loss: 0.486 | Acc: 83.073% (11803/14208)
120 391 Loss: 0.484 | Acc: 83.110% (12872/15488)
130 391 Loss: 0.484 | Acc: 83.123% (13938/16768)
140 391 Loss: 0.482 | Acc: 83.184% (15013/18048)
150 391 Loss: 0.483 | Acc: 83.133% (16068/19328)
160 391 Loss: 0.483 | Acc: 83.186% (17143/20608)
170 391 Loss: 0.485 | Acc: 83.173% (18205/21888)
180 391 Loss: 0.487 | Acc: 83.119% (19257/23168)
190 391 Loss: 0.486 | Acc: 83.189% (20338/24448)
200 391 Loss: 0.488 | Acc: 83.135% (21389/25728)
21

20 391 Loss: 0.474 | Acc: 84.152% (2262/2688)
30 391 Loss: 0.470 | Acc: 83.720% (3322/3968)
40 391 Loss: 0.460 | Acc: 84.280% (4423/5248)
50 391 Loss: 0.467 | Acc: 84.115% (5491/6528)
60 391 Loss: 0.471 | Acc: 83.837% (6546/7808)
70 391 Loss: 0.472 | Acc: 83.836% (7619/9088)
80 391 Loss: 0.472 | Acc: 83.690% (8677/10368)
90 391 Loss: 0.476 | Acc: 83.568% (9734/11648)
100 391 Loss: 0.476 | Acc: 83.547% (10801/12928)
110 391 Loss: 0.475 | Acc: 83.453% (11857/14208)
120 391 Loss: 0.477 | Acc: 83.536% (12938/15488)
130 391 Loss: 0.476 | Acc: 83.641% (14025/16768)
140 391 Loss: 0.479 | Acc: 83.511% (15072/18048)
150 391 Loss: 0.482 | Acc: 83.418% (16123/19328)
160 391 Loss: 0.482 | Acc: 83.434% (17194/20608)
170 391 Loss: 0.483 | Acc: 83.393% (18253/21888)
180 391 Loss: 0.484 | Acc: 83.326% (19305/23168)
190 391 Loss: 0.485 | Acc: 83.291% (20363/24448)
200 391 Loss: 0.485 | Acc: 83.314% (21435/25728)
210 391 Loss: 0.485 | Acc: 83.242% (22482/27008)
220 391 Loss: 0.487 | Acc: 83.159% (23524/

40 391 Loss: 0.476 | Acc: 83.918% (4404/5248)
50 391 Loss: 0.480 | Acc: 83.716% (5465/6528)
60 391 Loss: 0.479 | Acc: 83.594% (6527/7808)
70 391 Loss: 0.487 | Acc: 83.407% (7580/9088)
80 391 Loss: 0.489 | Acc: 83.247% (8631/10368)
90 391 Loss: 0.490 | Acc: 83.182% (9689/11648)
100 391 Loss: 0.491 | Acc: 83.207% (10757/12928)
110 391 Loss: 0.489 | Acc: 83.270% (11831/14208)
120 391 Loss: 0.489 | Acc: 83.252% (12894/15488)
130 391 Loss: 0.484 | Acc: 83.379% (13981/16768)
140 391 Loss: 0.484 | Acc: 83.372% (15047/18048)
150 391 Loss: 0.487 | Acc: 83.237% (16088/19328)
160 391 Loss: 0.488 | Acc: 83.210% (17148/20608)
170 391 Loss: 0.490 | Acc: 83.160% (18202/21888)
180 391 Loss: 0.489 | Acc: 83.153% (19265/23168)
190 391 Loss: 0.490 | Acc: 83.091% (20314/24448)
200 391 Loss: 0.491 | Acc: 83.077% (21374/25728)
210 391 Loss: 0.492 | Acc: 83.086% (22440/27008)
220 391 Loss: 0.491 | Acc: 83.109% (23510/28288)
230 391 Loss: 0.490 | Acc: 83.127% (24579/29568)
240 391 Loss: 0.489 | Acc: 83.137% (

60 391 Loss: 0.482 | Acc: 83.696% (6535/7808)
70 391 Loss: 0.481 | Acc: 83.660% (7603/9088)
80 391 Loss: 0.474 | Acc: 83.835% (8692/10368)
90 391 Loss: 0.479 | Acc: 83.654% (9744/11648)
100 391 Loss: 0.484 | Acc: 83.462% (10790/12928)
110 391 Loss: 0.482 | Acc: 83.523% (11867/14208)
120 391 Loss: 0.485 | Acc: 83.394% (12916/15488)
130 391 Loss: 0.487 | Acc: 83.427% (13989/16768)
140 391 Loss: 0.490 | Acc: 83.317% (15037/18048)
150 391 Loss: 0.489 | Acc: 83.371% (16114/19328)
160 391 Loss: 0.488 | Acc: 83.332% (17173/20608)
170 391 Loss: 0.489 | Acc: 83.205% (18212/21888)
180 391 Loss: 0.490 | Acc: 83.218% (19280/23168)
190 391 Loss: 0.489 | Acc: 83.213% (20344/24448)
200 391 Loss: 0.490 | Acc: 83.232% (21414/25728)
210 391 Loss: 0.489 | Acc: 83.194% (22469/27008)
220 391 Loss: 0.487 | Acc: 83.201% (23536/28288)
230 391 Loss: 0.487 | Acc: 83.201% (24601/29568)
240 391 Loss: 0.489 | Acc: 83.124% (25642/30848)
250 391 Loss: 0.488 | Acc: 83.136% (26710/32128)
260 391 Loss: 0.489 | Acc: 83.

80 391 Loss: 0.495 | Acc: 82.861% (8591/10368)
90 391 Loss: 0.497 | Acc: 82.907% (9657/11648)
100 391 Loss: 0.493 | Acc: 82.905% (10718/12928)
110 391 Loss: 0.491 | Acc: 82.925% (11782/14208)
120 391 Loss: 0.492 | Acc: 82.767% (12819/15488)
130 391 Loss: 0.492 | Acc: 82.783% (13881/16768)
140 391 Loss: 0.493 | Acc: 82.790% (14942/18048)
150 391 Loss: 0.492 | Acc: 82.838% (16011/19328)
160 391 Loss: 0.494 | Acc: 82.774% (17058/20608)
170 391 Loss: 0.495 | Acc: 82.744% (18111/21888)
180 391 Loss: 0.496 | Acc: 82.756% (19173/23168)
190 391 Loss: 0.496 | Acc: 82.714% (20222/24448)
200 391 Loss: 0.496 | Acc: 82.688% (21274/25728)
210 391 Loss: 0.496 | Acc: 82.746% (22348/27008)
220 391 Loss: 0.495 | Acc: 82.735% (23404/28288)
230 391 Loss: 0.493 | Acc: 82.782% (24477/29568)
240 391 Loss: 0.494 | Acc: 82.793% (25540/30848)
250 391 Loss: 0.493 | Acc: 82.834% (26613/32128)
260 391 Loss: 0.494 | Acc: 82.804% (27663/33408)
270 391 Loss: 0.494 | Acc: 82.836% (28734/34688)
280 391 Loss: 0.494 | Ac

...

160 391 Loss: 0.511 | Acc: 82.157% (16931/20608)
170 391 Loss: 0.511 | Acc: 82.150% (17981/21888)
180 391 Loss: 0.513 | Acc: 82.143% (19031/23168)
190 391 Loss: 0.515 | Acc: 82.093% (20070/24448)
200 391 Loss: 0.515 | Acc: 82.113% (21126/25728)
210 391 Loss: 0.516 | Acc: 82.076% (22167/27008)
220 391 Loss: 0.518 | Acc: 82.003% (23197/28288)
230 391 Loss: 0.518 | Acc: 82.008% (24248/29568)
240 391 Loss: 0.520 | Acc: 81.902% (25265/30848)
250 391 Loss: 0.522 | Acc: 81.848% (26296/32128)
260 391 Loss: 0.523 | Acc: 81.795% (27326/33408)
270 391 Loss: 0.524 | Acc: 81.780% (28368/34688)
280 391 Loss: 0.523 | Acc: 81.778% (29414/35968)
290 391 Loss: 0.523 | Acc: 81.795% (30467/37248)
300 391 Loss: 0.523 | Acc: 81.779% (31508/38528)
310 391 Loss: 0.522 | Acc: 81.835% (32577/39808)
320 391 Loss: 0.522 | Acc: 81.844% (33628/41088)
330 391 Loss: 0.522 | Acc: 81.828% (34669/42368)
340 391 Loss: 0.522 | Acc: 81.823% (35714/43648)
350 391 Loss: 0.521 | Acc: 81.851% (36774/44928)
360 391 Loss: 0.522 

180 391 Loss: 0.532 | Acc: 81.608% (18907/23168)
190 391 Loss: 0.531 | Acc: 81.675% (19968/24448)
200 391 Loss: 0.533 | Acc: 81.604% (20995/25728)
210 391 Loss: 0.534 | Acc: 81.561% (22028/27008)
220 391 Loss: 0.533 | Acc: 81.646% (23096/28288)
230 391 Loss: 0.535 | Acc: 81.605% (24129/29568)
240 391 Loss: 0.536 | Acc: 81.564% (25161/30848)
250 391 Loss: 0.536 | Acc: 81.611% (26220/32128)
260 391 Loss: 0.534 | Acc: 81.657% (27280/33408)
270 391 Loss: 0.536 | Acc: 81.590% (28302/34688)
280 391 Loss: 0.537 | Acc: 81.545% (29330/35968)
290 391 Loss: 0.536 | Acc: 81.569% (30383/37248)
300 391 Loss: 0.535 | Acc: 81.580% (31431/38528)
310 391 Loss: 0.535 | Acc: 81.554% (32465/39808)
320 391 Loss: 0.536 | Acc: 81.513% (33492/41088)
330 391 Loss: 0.536 | Acc: 81.474% (34519/42368)
340 391 Loss: 0.536 | Acc: 81.500% (35573/43648)
350 391 Loss: 0.537 | Acc: 81.448% (36593/44928)
360 391 Loss: 0.536 | Acc: 81.479% (37650/46208)
370 391 Loss: 0.536 | Acc: 81.473% (38690/47488)
380 391 Loss: 0.535 

200 391 Loss: 0.552 | Acc: 80.737% (20772/25728)
210 391 Loss: 0.550 | Acc: 80.802% (21823/27008)
220 391 Loss: 0.549 | Acc: 80.790% (22854/28288)
230 391 Loss: 0.547 | Acc: 80.848% (23905/29568)
240 391 Loss: 0.547 | Acc: 80.851% (24941/30848)
250 391 Loss: 0.545 | Acc: 80.939% (26004/32128)
260 391 Loss: 0.545 | Acc: 80.924% (27035/33408)
270 391 Loss: 0.546 | Acc: 80.950% (28080/34688)
280 391 Loss: 0.547 | Acc: 80.894% (29096/35968)
290 391 Loss: 0.547 | Acc: 80.877% (30125/37248)
300 391 Loss: 0.548 | Acc: 80.850% (31150/38528)
310 391 Loss: 0.550 | Acc: 80.793% (32162/39808)
320 391 Loss: 0.550 | Acc: 80.795% (33197/41088)
330 391 Loss: 0.549 | Acc: 80.872% (34264/42368)
340 391 Loss: 0.547 | Acc: 80.906% (35314/43648)
350 391 Loss: 0.547 | Acc: 80.914% (36353/44928)
360 391 Loss: 0.548 | Acc: 80.897% (37381/46208)
370 391 Loss: 0.548 | Acc: 80.879% (38408/47488)
380 391 Loss: 0.548 | Acc: 80.897% (39452/48768)
390 391 Loss: 0.548 | Acc: 80.894% (40447/50000)
0 100 Loss: 0.502 | 

220 391 Loss: 0.552 | Acc: 80.882% (22880/28288)
230 391 Loss: 0.553 | Acc: 80.871% (23912/29568)
240 391 Loss: 0.555 | Acc: 80.812% (24929/30848)
250 391 Loss: 0.556 | Acc: 80.727% (25936/32128)
260 391 Loss: 0.555 | Acc: 80.726% (26969/33408)
270 391 Loss: 0.554 | Acc: 80.740% (28007/34688)
280 391 Loss: 0.553 | Acc: 80.786% (29057/35968)
290 391 Loss: 0.555 | Acc: 80.737% (30073/37248)
300 391 Loss: 0.558 | Acc: 80.682% (31085/38528)
310 391 Loss: 0.557 | Acc: 80.722% (32134/39808)
320 391 Loss: 0.557 | Acc: 80.693% (33155/41088)
330 391 Loss: 0.557 | Acc: 80.733% (34205/42368)
340 391 Loss: 0.556 | Acc: 80.728% (35236/43648)
350 391 Loss: 0.556 | Acc: 80.725% (36268/44928)
360 391 Loss: 0.556 | Acc: 80.709% (37294/46208)
370 391 Loss: 0.558 | Acc: 80.688% (38317/47488)
380 391 Loss: 0.558 | Acc: 80.653% (39333/48768)
390 391 Loss: 0.558 | Acc: 80.650% (40325/50000)
0 100 Loss: 0.679 | Acc: 79.000% (79/100)
50 100 Loss: 0.609 | Acc: 79.569% (4058/5100)
epoch :  44 82.93
0 391 Loss: 

KeyboardInterrupt: 

In [ ]:
best_accuracy

### Adam 사용 시 성능이 더 저하

## dropout 2개( 1 , 2n 사이 / 2n , 4n 사이) & 0.5 & opt : sgd 

In [14]:
best_accuracy = 0
start_epoch = 0

net = resnet20()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True
    
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 4.614 | Acc: 6.250% (8/128)
10 391 Loss: 3.054 | Acc: 9.872% (139/1408)
20 391 Loss: 2.865 | Acc: 11.756% (316/2688)
30 391 Loss: 2.680 | Acc: 13.180% (523/3968)
40 391 Loss: 2.559 | Acc: 14.158% (743/5248)
50 391 Loss: 2.462 | Acc: 16.023% (1046/6528)
60 391 Loss: 2.395 | Acc: 17.392% (1358/7808)
70 391 Loss: 2.344 | Acc: 18.321% (1665/9088)
80 391 Loss: 2.297 | Acc: 19.309% (2002/10368)
90 391 Loss: 2.261 | Acc: 19.961% (2325/11648)
100 391 Loss: 2.229 | Acc: 20.475% (2647/12928)
110 391 Loss: 2.199 | Acc: 21.171% (3008/14208)
120 391 Loss: 2.178 | Acc: 21.726% (3365/15488)
130 391 Loss: 2.159 | Acc: 22.179% (3719/16768)
140 391 Loss: 2.140 | Acc: 22.701% (4097/18048)
150 391 Loss: 2.123 | Acc: 23.148% (4474/19328)
160 391 Loss: 2.112 | Acc: 23.384% (4819/20608)
170 391 Loss: 2.097 | Acc: 23.840% (5218/21888)
180 391 Loss: 2.085 | Acc: 24.176% (5601/23168)
190 391 Loss: 2.071 | Acc: 24.546% (6001/24448)
200 391 Loss: 2.060 | Acc: 24.868% (6398/25728)
210 391 Loss: 2.051 |

20 391 Loss: 1.274 | Acc: 53.609% (1441/2688)
30 391 Loss: 1.270 | Acc: 53.705% (2131/3968)
40 391 Loss: 1.271 | Acc: 54.002% (2834/5248)
50 391 Loss: 1.268 | Acc: 54.044% (3528/6528)
60 391 Loss: 1.264 | Acc: 54.367% (4245/7808)
70 391 Loss: 1.262 | Acc: 54.478% (4951/9088)
80 391 Loss: 1.261 | Acc: 54.620% (5663/10368)
90 391 Loss: 1.263 | Acc: 54.507% (6349/11648)
100 391 Loss: 1.263 | Acc: 54.339% (7025/12928)
110 391 Loss: 1.264 | Acc: 54.378% (7726/14208)
120 391 Loss: 1.262 | Acc: 54.552% (8449/15488)
130 391 Loss: 1.260 | Acc: 54.598% (9155/16768)
140 391 Loss: 1.262 | Acc: 54.499% (9836/18048)
150 391 Loss: 1.261 | Acc: 54.594% (10552/19328)
160 391 Loss: 1.262 | Acc: 54.537% (11239/20608)
170 391 Loss: 1.262 | Acc: 54.500% (11929/21888)
180 391 Loss: 1.261 | Acc: 54.489% (12624/23168)
190 391 Loss: 1.264 | Acc: 54.266% (13267/24448)
200 391 Loss: 1.262 | Acc: 54.209% (13947/25728)
210 391 Loss: 1.259 | Acc: 54.258% (14654/27008)
220 391 Loss: 1.257 | Acc: 54.295% (15359/28288

30 391 Loss: 0.970 | Acc: 65.146% (2585/3968)
40 391 Loss: 0.979 | Acc: 65.168% (3420/5248)
50 391 Loss: 0.980 | Acc: 65.012% (4244/6528)
60 391 Loss: 0.988 | Acc: 64.536% (5039/7808)
70 391 Loss: 0.987 | Acc: 64.536% (5865/9088)
80 391 Loss: 0.987 | Acc: 64.400% (6677/10368)
90 391 Loss: 0.991 | Acc: 64.380% (7499/11648)
100 391 Loss: 0.990 | Acc: 64.287% (8311/12928)
110 391 Loss: 0.989 | Acc: 64.471% (9160/14208)
120 391 Loss: 0.990 | Acc: 64.385% (9972/15488)
130 391 Loss: 0.988 | Acc: 64.486% (10813/16768)
140 391 Loss: 0.991 | Acc: 64.412% (11625/18048)
150 391 Loss: 0.993 | Acc: 64.409% (12449/19328)
160 391 Loss: 0.993 | Acc: 64.431% (13278/20608)
170 391 Loss: 0.992 | Acc: 64.451% (14107/21888)
180 391 Loss: 0.993 | Acc: 64.416% (14924/23168)
190 391 Loss: 0.993 | Acc: 64.455% (15758/24448)
200 391 Loss: 0.994 | Acc: 64.424% (16575/25728)
210 391 Loss: 0.995 | Acc: 64.429% (17401/27008)
220 391 Loss: 0.994 | Acc: 64.501% (18246/28288)
230 391 Loss: 0.994 | Acc: 64.597% (19100/

40 391 Loss: 0.853 | Acc: 69.912% (3669/5248)
50 391 Loss: 0.858 | Acc: 69.884% (4562/6528)
60 391 Loss: 0.853 | Acc: 70.082% (5472/7808)
70 391 Loss: 0.853 | Acc: 70.169% (6377/9088)
80 391 Loss: 0.851 | Acc: 70.332% (7292/10368)
90 391 Loss: 0.856 | Acc: 70.201% (8177/11648)
100 391 Loss: 0.855 | Acc: 70.135% (9067/12928)
110 391 Loss: 0.854 | Acc: 70.193% (9973/14208)
120 391 Loss: 0.853 | Acc: 70.158% (10866/15488)
130 391 Loss: 0.850 | Acc: 70.378% (11801/16768)
140 391 Loss: 0.848 | Acc: 70.296% (12687/18048)
150 391 Loss: 0.847 | Acc: 70.416% (13610/19328)
160 391 Loss: 0.848 | Acc: 70.322% (14492/20608)
170 391 Loss: 0.848 | Acc: 70.386% (15406/21888)
180 391 Loss: 0.849 | Acc: 70.278% (16282/23168)
190 391 Loss: 0.850 | Acc: 70.083% (17134/24448)
200 391 Loss: 0.851 | Acc: 70.153% (18049/25728)
210 391 Loss: 0.851 | Acc: 70.135% (18942/27008)
220 391 Loss: 0.849 | Acc: 70.153% (19845/28288)
230 391 Loss: 0.851 | Acc: 70.130% (20736/29568)
240 391 Loss: 0.851 | Acc: 70.160% (21

60 391 Loss: 0.723 | Acc: 74.129% (5788/7808)
70 391 Loss: 0.725 | Acc: 74.076% (6732/9088)
80 391 Loss: 0.720 | Acc: 74.421% (7716/10368)
90 391 Loss: 0.722 | Acc: 74.262% (8650/11648)
100 391 Loss: 0.722 | Acc: 74.327% (9609/12928)
110 391 Loss: 0.719 | Acc: 74.634% (10604/14208)
120 391 Loss: 0.718 | Acc: 74.677% (11566/15488)
130 391 Loss: 0.718 | Acc: 74.755% (12535/16768)
140 391 Loss: 0.721 | Acc: 74.717% (13485/18048)
150 391 Loss: 0.722 | Acc: 74.762% (14450/19328)
160 391 Loss: 0.722 | Acc: 74.796% (15414/20608)
170 391 Loss: 0.722 | Acc: 74.735% (16358/21888)
180 391 Loss: 0.724 | Acc: 74.629% (17290/23168)
190 391 Loss: 0.726 | Acc: 74.550% (18226/24448)
200 391 Loss: 0.727 | Acc: 74.499% (19167/25728)
210 391 Loss: 0.726 | Acc: 74.570% (20140/27008)
220 391 Loss: 0.725 | Acc: 74.586% (21099/28288)
230 391 Loss: 0.726 | Acc: 74.570% (22049/29568)
240 391 Loss: 0.728 | Acc: 74.530% (22991/30848)
250 391 Loss: 0.728 | Acc: 74.490% (23932/32128)
260 391 Loss: 0.728 | Acc: 74.4

...

70 391 Loss: 0.119 | Acc: 96.006% (8725/9088)
80 391 Loss: 0.120 | Acc: 95.959% (9949/10368)
90 391 Loss: 0.121 | Acc: 95.956% (11177/11648)
100 391 Loss: 0.121 | Acc: 95.993% (12410/12928)
110 391 Loss: 0.123 | Acc: 95.981% (13637/14208)
120 391 Loss: 0.123 | Acc: 96.016% (14871/15488)
130 391 Loss: 0.122 | Acc: 96.088% (16112/16768)
140 391 Loss: 0.122 | Acc: 96.038% (17333/18048)
150 391 Loss: 0.121 | Acc: 96.047% (18564/19328)
160 391 Loss: 0.122 | Acc: 96.021% (19788/20608)
170 391 Loss: 0.122 | Acc: 96.016% (21016/21888)
180 391 Loss: 0.121 | Acc: 96.007% (22243/23168)
190 391 Loss: 0.121 | Acc: 96.016% (23474/24448)
200 391 Loss: 0.121 | Acc: 96.047% (24711/25728)
210 391 Loss: 0.121 | Acc: 96.049% (25941/27008)
220 391 Loss: 0.122 | Acc: 95.970% (27148/28288)
230 391 Loss: 0.122 | Acc: 95.979% (28379/29568)
240 391 Loss: 0.122 | Acc: 95.990% (29611/30848)
250 391 Loss: 0.122 | Acc: 95.972% (30834/32128)
260 391 Loss: 0.122 | Acc: 95.986% (32067/33408)
270 391 Loss: 0.122 | Acc:

80 391 Loss: 0.121 | Acc: 95.978% (9951/10368)
90 391 Loss: 0.119 | Acc: 96.059% (11189/11648)
100 391 Loss: 0.119 | Acc: 96.071% (12420/12928)
110 391 Loss: 0.118 | Acc: 96.136% (13659/14208)
120 391 Loss: 0.118 | Acc: 96.132% (14889/15488)
130 391 Loss: 0.116 | Acc: 96.225% (16135/16768)
140 391 Loss: 0.117 | Acc: 96.171% (17357/18048)
150 391 Loss: 0.117 | Acc: 96.192% (18592/19328)
160 391 Loss: 0.118 | Acc: 96.147% (19814/20608)
170 391 Loss: 0.118 | Acc: 96.149% (21045/21888)
180 391 Loss: 0.118 | Acc: 96.085% (22261/23168)
190 391 Loss: 0.118 | Acc: 96.090% (23492/24448)
200 391 Loss: 0.118 | Acc: 96.094% (24723/25728)
210 391 Loss: 0.118 | Acc: 96.064% (25945/27008)
220 391 Loss: 0.119 | Acc: 96.069% (27176/28288)
230 391 Loss: 0.119 | Acc: 96.073% (28407/29568)
240 391 Loss: 0.118 | Acc: 96.081% (29639/30848)
250 391 Loss: 0.117 | Acc: 96.128% (30884/32128)
260 391 Loss: 0.117 | Acc: 96.145% (32120/33408)
270 391 Loss: 0.117 | Acc: 96.134% (33347/34688)
280 391 Loss: 0.118 | A

90 391 Loss: 0.121 | Acc: 95.913% (11172/11648)
100 391 Loss: 0.121 | Acc: 95.900% (12398/12928)
110 391 Loss: 0.121 | Acc: 95.932% (13630/14208)
120 391 Loss: 0.120 | Acc: 95.971% (14864/15488)
130 391 Loss: 0.121 | Acc: 95.897% (16080/16768)
140 391 Loss: 0.121 | Acc: 95.950% (17317/18048)
150 391 Loss: 0.119 | Acc: 96.068% (18568/19328)
160 391 Loss: 0.119 | Acc: 96.045% (19793/20608)
170 391 Loss: 0.119 | Acc: 96.057% (21025/21888)
180 391 Loss: 0.118 | Acc: 96.128% (22271/23168)
190 391 Loss: 0.117 | Acc: 96.151% (23507/24448)
200 391 Loss: 0.117 | Acc: 96.140% (24735/25728)
210 391 Loss: 0.117 | Acc: 96.127% (25962/27008)
220 391 Loss: 0.117 | Acc: 96.136% (27195/28288)
230 391 Loss: 0.117 | Acc: 96.131% (28424/29568)
240 391 Loss: 0.117 | Acc: 96.142% (29658/30848)
250 391 Loss: 0.116 | Acc: 96.184% (30902/32128)
260 391 Loss: 0.116 | Acc: 96.163% (32126/33408)
270 391 Loss: 0.116 | Acc: 96.154% (33354/34688)
280 391 Loss: 0.117 | Acc: 96.144% (34581/35968)
290 391 Loss: 0.116 |

100 391 Loss: 0.118 | Acc: 96.086% (12422/12928)
110 391 Loss: 0.118 | Acc: 96.080% (13651/14208)
120 391 Loss: 0.118 | Acc: 96.049% (14876/15488)
130 391 Loss: 0.117 | Acc: 96.106% (16115/16768)
140 391 Loss: 0.116 | Acc: 96.127% (17349/18048)
150 391 Loss: 0.116 | Acc: 96.156% (18585/19328)
160 391 Loss: 0.117 | Acc: 96.123% (19809/20608)
170 391 Loss: 0.118 | Acc: 96.098% (21034/21888)
180 391 Loss: 0.116 | Acc: 96.163% (22279/23168)
190 391 Loss: 0.116 | Acc: 96.200% (23519/24448)
200 391 Loss: 0.116 | Acc: 96.226% (24757/25728)
210 391 Loss: 0.115 | Acc: 96.260% (25998/27008)
220 391 Loss: 0.115 | Acc: 96.263% (27231/28288)
230 391 Loss: 0.114 | Acc: 96.283% (28469/29568)
240 391 Loss: 0.114 | Acc: 96.308% (29709/30848)
250 391 Loss: 0.114 | Acc: 96.327% (30948/32128)
260 391 Loss: 0.114 | Acc: 96.303% (32173/33408)
270 391 Loss: 0.114 | Acc: 96.321% (33412/34688)
280 391 Loss: 0.114 | Acc: 96.305% (34639/35968)
290 391 Loss: 0.113 | Acc: 96.343% (35886/37248)
300 391 Loss: 0.113 

110 391 Loss: 0.115 | Acc: 96.206% (13669/14208)
120 391 Loss: 0.115 | Acc: 96.191% (14898/15488)
130 391 Loss: 0.114 | Acc: 96.201% (16131/16768)
140 391 Loss: 0.113 | Acc: 96.249% (17371/18048)
150 391 Loss: 0.112 | Acc: 96.275% (18608/19328)
160 391 Loss: 0.113 | Acc: 96.259% (19837/20608)
170 391 Loss: 0.113 | Acc: 96.267% (21071/21888)
180 391 Loss: 0.113 | Acc: 96.245% (22298/23168)
190 391 Loss: 0.113 | Acc: 96.294% (23542/24448)
200 391 Loss: 0.113 | Acc: 96.276% (24770/25728)
210 391 Loss: 0.113 | Acc: 96.223% (25988/27008)
220 391 Loss: 0.114 | Acc: 96.242% (27225/28288)
230 391 Loss: 0.113 | Acc: 96.239% (28456/29568)
240 391 Loss: 0.114 | Acc: 96.217% (29681/30848)
250 391 Loss: 0.113 | Acc: 96.268% (30929/32128)
260 391 Loss: 0.113 | Acc: 96.270% (32162/33408)
270 391 Loss: 0.113 | Acc: 96.241% (33384/34688)
280 391 Loss: 0.113 | Acc: 96.211% (34605/35968)
290 391 Loss: 0.113 | Acc: 96.207% (35835/37248)
300 391 Loss: 0.114 | Acc: 96.211% (37068/38528)
310 391 Loss: 0.114 

In [15]:
best_accuracy

87.83

## dropout 2개(  2n , 4n 사이 / 4n , 6n 사이) & 0.5 & opt : sgd 

In [18]:
best_accuracy = 0
start_epoch = 0

net = resnet20()
net = net.to(device)
if device == 'cuda':
    net = torch.nn.DataParallel(net)
    cudnn.benchmark = True
    
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)

for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()
    print('epoch : ',epoch, best_accuracy)

0 391 Loss: 4.482 | Acc: 8.594% (11/128)
10 391 Loss: 3.071 | Acc: 11.222% (158/1408)
20 391 Loss: 2.831 | Acc: 13.207% (355/2688)
30 391 Loss: 2.661 | Acc: 14.919% (592/3968)
40 391 Loss: 2.532 | Acc: 16.311% (856/5248)
50 391 Loss: 2.444 | Acc: 17.739% (1158/6528)
60 391 Loss: 2.375 | Acc: 18.852% (1472/7808)
70 391 Loss: 2.320 | Acc: 19.729% (1793/9088)
80 391 Loss: 2.275 | Acc: 20.448% (2120/10368)
90 391 Loss: 2.239 | Acc: 20.905% (2435/11648)
100 391 Loss: 2.203 | Acc: 21.744% (2811/12928)
110 391 Loss: 2.177 | Acc: 22.199% (3154/14208)
120 391 Loss: 2.153 | Acc: 22.656% (3509/15488)
130 391 Loss: 2.130 | Acc: 23.247% (3898/16768)
140 391 Loss: 2.111 | Acc: 23.609% (4261/18048)
150 391 Loss: 2.096 | Acc: 23.872% (4614/19328)
160 391 Loss: 2.078 | Acc: 24.398% (5028/20608)
170 391 Loss: 2.061 | Acc: 24.845% (5438/21888)
180 391 Loss: 2.045 | Acc: 25.289% (5859/23168)
190 391 Loss: 2.033 | Acc: 25.556% (6248/24448)
200 391 Loss: 2.020 | Acc: 25.952% (6677/25728)
210 391 Loss: 2.008

20 391 Loss: 1.158 | Acc: 57.812% (1554/2688)
30 391 Loss: 1.162 | Acc: 57.611% (2286/3968)
40 391 Loss: 1.166 | Acc: 58.079% (3048/5248)
50 391 Loss: 1.162 | Acc: 57.966% (3784/6528)
60 391 Loss: 1.166 | Acc: 57.633% (4500/7808)
70 391 Loss: 1.173 | Acc: 57.284% (5206/9088)
80 391 Loss: 1.180 | Acc: 56.964% (5906/10368)
90 391 Loss: 1.184 | Acc: 56.782% (6614/11648)
100 391 Loss: 1.184 | Acc: 56.552% (7311/12928)
110 391 Loss: 1.185 | Acc: 56.658% (8050/14208)
120 391 Loss: 1.186 | Acc: 56.508% (8752/15488)
130 391 Loss: 1.189 | Acc: 56.399% (9457/16768)
140 391 Loss: 1.189 | Acc: 56.433% (10185/18048)
150 391 Loss: 1.189 | Acc: 56.452% (10911/19328)
160 391 Loss: 1.187 | Acc: 56.561% (11656/20608)
170 391 Loss: 1.187 | Acc: 56.529% (12373/21888)
180 391 Loss: 1.188 | Acc: 56.518% (13094/23168)
190 391 Loss: 1.185 | Acc: 56.671% (13855/24448)
200 391 Loss: 1.183 | Acc: 56.740% (14598/25728)
210 391 Loss: 1.183 | Acc: 56.776% (15334/27008)
220 391 Loss: 1.180 | Acc: 56.900% (16096/2828

40 391 Loss: 0.962 | Acc: 64.996% (3411/5248)
50 391 Loss: 0.974 | Acc: 64.583% (4216/6528)
60 391 Loss: 0.970 | Acc: 64.908% (5068/7808)
70 391 Loss: 0.964 | Acc: 65.097% (5916/9088)
80 391 Loss: 0.966 | Acc: 65.008% (6740/10368)
90 391 Loss: 0.966 | Acc: 65.204% (7595/11648)
100 391 Loss: 0.964 | Acc: 65.223% (8432/12928)
110 391 Loss: 0.968 | Acc: 65.118% (9252/14208)
120 391 Loss: 0.966 | Acc: 65.263% (10108/15488)
130 391 Loss: 0.966 | Acc: 65.297% (10949/16768)
140 391 Loss: 0.966 | Acc: 65.265% (11779/18048)
150 391 Loss: 0.967 | Acc: 65.201% (12602/19328)
160 391 Loss: 0.968 | Acc: 65.169% (13430/20608)
170 391 Loss: 0.971 | Acc: 65.077% (14244/21888)
180 391 Loss: 0.972 | Acc: 64.960% (15050/23168)
190 391 Loss: 0.971 | Acc: 64.966% (15883/24448)
200 391 Loss: 0.970 | Acc: 65.093% (16747/25728)
210 391 Loss: 0.968 | Acc: 65.177% (17603/27008)
220 391 Loss: 0.969 | Acc: 65.176% (18437/28288)
230 391 Loss: 0.967 | Acc: 65.233% (19288/29568)
240 391 Loss: 0.969 | Acc: 65.184% (20

60 391 Loss: 0.871 | Acc: 69.262% (5408/7808)
70 391 Loss: 0.865 | Acc: 69.476% (6314/9088)
80 391 Loss: 0.867 | Acc: 69.416% (7197/10368)
90 391 Loss: 0.865 | Acc: 69.334% (8076/11648)
100 391 Loss: 0.864 | Acc: 69.400% (8972/12928)
110 391 Loss: 0.863 | Acc: 69.447% (9867/14208)
120 391 Loss: 0.861 | Acc: 69.551% (10772/15488)
130 391 Loss: 0.858 | Acc: 69.591% (11669/16768)
140 391 Loss: 0.857 | Acc: 69.620% (12565/18048)
150 391 Loss: 0.856 | Acc: 69.635% (13459/19328)
160 391 Loss: 0.858 | Acc: 69.638% (14351/20608)
170 391 Loss: 0.859 | Acc: 69.627% (15240/21888)
180 391 Loss: 0.861 | Acc: 69.531% (16109/23168)
190 391 Loss: 0.862 | Acc: 69.470% (16984/24448)
200 391 Loss: 0.861 | Acc: 69.555% (17895/25728)
210 391 Loss: 0.861 | Acc: 69.565% (18788/27008)
220 391 Loss: 0.861 | Acc: 69.524% (19667/28288)
230 391 Loss: 0.861 | Acc: 69.541% (20562/29568)
240 391 Loss: 0.861 | Acc: 69.512% (21443/30848)
250 391 Loss: 0.860 | Acc: 69.603% (22362/32128)
260 391 Loss: 0.859 | Acc: 69.59

80 391 Loss: 0.778 | Acc: 72.328% (7499/10368)
90 391 Loss: 0.775 | Acc: 72.364% (8429/11648)
100 391 Loss: 0.776 | Acc: 72.362% (9355/12928)
110 391 Loss: 0.774 | Acc: 72.473% (10297/14208)
120 391 Loss: 0.782 | Acc: 72.211% (11184/15488)
130 391 Loss: 0.779 | Acc: 72.364% (12134/16768)
140 391 Loss: 0.775 | Acc: 72.507% (13086/18048)
150 391 Loss: 0.775 | Acc: 72.579% (14028/19328)
160 391 Loss: 0.775 | Acc: 72.564% (14954/20608)
170 391 Loss: 0.773 | Acc: 72.638% (15899/21888)
180 391 Loss: 0.772 | Acc: 72.730% (16850/23168)
190 391 Loss: 0.772 | Acc: 72.726% (17780/24448)
200 391 Loss: 0.772 | Acc: 72.742% (18715/25728)
210 391 Loss: 0.773 | Acc: 72.734% (19644/27008)
220 391 Loss: 0.771 | Acc: 72.755% (20581/28288)
230 391 Loss: 0.772 | Acc: 72.737% (21507/29568)
240 391 Loss: 0.771 | Acc: 72.779% (22451/30848)
250 391 Loss: 0.773 | Acc: 72.765% (23378/32128)
260 391 Loss: 0.772 | Acc: 72.815% (24326/33408)
270 391 Loss: 0.772 | Acc: 72.780% (25246/34688)
280 391 Loss: 0.772 | Acc

...

110 391 Loss: 0.156 | Acc: 94.735% (13460/14208)
120 391 Loss: 0.159 | Acc: 94.622% (14655/15488)
130 391 Loss: 0.159 | Acc: 94.627% (15867/16768)
140 391 Loss: 0.158 | Acc: 94.614% (17076/18048)
150 391 Loss: 0.157 | Acc: 94.640% (18292/19328)
160 391 Loss: 0.157 | Acc: 94.619% (19499/20608)
170 391 Loss: 0.157 | Acc: 94.618% (20710/21888)
180 391 Loss: 0.157 | Acc: 94.622% (21922/23168)
190 391 Loss: 0.157 | Acc: 94.642% (23138/24448)
200 391 Loss: 0.157 | Acc: 94.605% (24340/25728)
210 391 Loss: 0.157 | Acc: 94.583% (25545/27008)
220 391 Loss: 0.158 | Acc: 94.552% (26747/28288)
230 391 Loss: 0.158 | Acc: 94.538% (27953/29568)
240 391 Loss: 0.156 | Acc: 94.603% (29183/30848)
250 391 Loss: 0.156 | Acc: 94.597% (30392/32128)
260 391 Loss: 0.156 | Acc: 94.597% (31603/33408)
270 391 Loss: 0.156 | Acc: 94.589% (32811/34688)
280 391 Loss: 0.155 | Acc: 94.626% (34035/35968)
290 391 Loss: 0.154 | Acc: 94.660% (35259/37248)
300 391 Loss: 0.154 | Acc: 94.640% (36463/38528)
310 391 Loss: 0.154 

120 391 Loss: 0.157 | Acc: 94.686% (14665/15488)
130 391 Loss: 0.156 | Acc: 94.764% (15890/16768)
140 391 Loss: 0.156 | Acc: 94.747% (17100/18048)
150 391 Loss: 0.156 | Acc: 94.790% (18321/19328)
160 391 Loss: 0.155 | Acc: 94.822% (19541/20608)
170 391 Loss: 0.155 | Acc: 94.842% (20759/21888)
180 391 Loss: 0.154 | Acc: 94.864% (21978/23168)
190 391 Loss: 0.153 | Acc: 94.858% (23191/24448)
200 391 Loss: 0.152 | Acc: 94.873% (24409/25728)
210 391 Loss: 0.153 | Acc: 94.839% (25614/27008)
220 391 Loss: 0.152 | Acc: 94.874% (26838/28288)
230 391 Loss: 0.151 | Acc: 94.900% (28060/29568)
240 391 Loss: 0.151 | Acc: 94.920% (29281/30848)
250 391 Loss: 0.151 | Acc: 94.905% (30491/32128)
260 391 Loss: 0.151 | Acc: 94.905% (31706/33408)
270 391 Loss: 0.151 | Acc: 94.889% (32915/34688)
280 391 Loss: 0.152 | Acc: 94.876% (34125/35968)
290 391 Loss: 0.152 | Acc: 94.867% (35336/37248)
300 391 Loss: 0.152 | Acc: 94.869% (36551/38528)
310 391 Loss: 0.152 | Acc: 94.863% (37763/39808)
320 391 Loss: 0.153 

130 391 Loss: 0.151 | Acc: 94.841% (15903/16768)
140 391 Loss: 0.151 | Acc: 94.902% (17128/18048)
150 391 Loss: 0.150 | Acc: 94.924% (18347/19328)
160 391 Loss: 0.150 | Acc: 94.939% (19565/20608)
170 391 Loss: 0.150 | Acc: 94.942% (20781/21888)
180 391 Loss: 0.149 | Acc: 94.980% (22005/23168)
190 391 Loss: 0.149 | Acc: 94.981% (23221/24448)
200 391 Loss: 0.148 | Acc: 94.998% (24441/25728)
210 391 Loss: 0.150 | Acc: 94.924% (25637/27008)
220 391 Loss: 0.149 | Acc: 94.959% (26862/28288)
230 391 Loss: 0.149 | Acc: 94.991% (28087/29568)
240 391 Loss: 0.150 | Acc: 94.969% (29296/30848)
250 391 Loss: 0.150 | Acc: 94.942% (30503/32128)
260 391 Loss: 0.149 | Acc: 94.974% (31729/33408)
270 391 Loss: 0.149 | Acc: 94.964% (32941/34688)
280 391 Loss: 0.149 | Acc: 94.984% (34164/35968)
290 391 Loss: 0.149 | Acc: 94.969% (35374/37248)
300 391 Loss: 0.149 | Acc: 94.954% (36584/38528)
310 391 Loss: 0.150 | Acc: 94.933% (37791/39808)
320 391 Loss: 0.150 | Acc: 94.916% (38999/41088)
330 391 Loss: 0.150 

140 391 Loss: 0.146 | Acc: 95.019% (17149/18048)
150 391 Loss: 0.148 | Acc: 94.930% (18348/19328)
160 391 Loss: 0.147 | Acc: 94.963% (19570/20608)
170 391 Loss: 0.147 | Acc: 94.920% (20776/21888)
180 391 Loss: 0.145 | Acc: 94.976% (22004/23168)
190 391 Loss: 0.145 | Acc: 94.998% (23225/24448)
200 391 Loss: 0.145 | Acc: 94.990% (24439/25728)
210 391 Loss: 0.146 | Acc: 94.942% (25642/27008)
220 391 Loss: 0.146 | Acc: 94.955% (26861/28288)
230 391 Loss: 0.146 | Acc: 94.968% (28080/29568)
240 391 Loss: 0.146 | Acc: 94.959% (29293/30848)
250 391 Loss: 0.147 | Acc: 94.920% (30496/32128)
260 391 Loss: 0.147 | Acc: 94.914% (31709/33408)
270 391 Loss: 0.147 | Acc: 94.912% (32923/34688)
280 391 Loss: 0.147 | Acc: 94.912% (34138/35968)
290 391 Loss: 0.148 | Acc: 94.875% (35339/37248)
300 391 Loss: 0.148 | Acc: 94.871% (36552/38528)
310 391 Loss: 0.149 | Acc: 94.868% (37765/39808)
320 391 Loss: 0.148 | Acc: 94.906% (38995/41088)
330 391 Loss: 0.147 | Acc: 94.923% (40217/42368)
340 391 Loss: 0.147 

150 391 Loss: 0.147 | Acc: 94.847% (18332/19328)
160 391 Loss: 0.148 | Acc: 94.837% (19544/20608)
170 391 Loss: 0.148 | Acc: 94.833% (20757/21888)
180 391 Loss: 0.150 | Acc: 94.790% (21961/23168)
190 391 Loss: 0.149 | Acc: 94.797% (23176/24448)
200 391 Loss: 0.149 | Acc: 94.799% (24390/25728)
210 391 Loss: 0.149 | Acc: 94.824% (25610/27008)
220 391 Loss: 0.150 | Acc: 94.818% (26822/28288)
230 391 Loss: 0.151 | Acc: 94.771% (28022/29568)
240 391 Loss: 0.151 | Acc: 94.758% (29231/30848)
250 391 Loss: 0.151 | Acc: 94.755% (30443/32128)
260 391 Loss: 0.151 | Acc: 94.783% (31665/33408)
270 391 Loss: 0.151 | Acc: 94.785% (32879/34688)
280 391 Loss: 0.151 | Acc: 94.790% (34094/35968)
290 391 Loss: 0.150 | Acc: 94.776% (35302/37248)
300 391 Loss: 0.151 | Acc: 94.736% (36500/38528)
310 391 Loss: 0.151 | Acc: 94.722% (37707/39808)
320 391 Loss: 0.151 | Acc: 94.733% (38924/41088)
330 391 Loss: 0.150 | Acc: 94.770% (40152/42368)
340 391 Loss: 0.150 | Acc: 94.792% (41375/43648)
350 391 Loss: 0.150 

In [19]:
best_accuracy

90.2